#####Libraries
***

In [ ]:
import sklearn
import seaborn as sns
import pandas as pd
import numpy as np
import seaborn as sns
!pip install yfinance --upgrade --no-cache-dir
import yfinance as yf
from pandas_datareader import data as pdr
yf.pdr_override()
# pip install TA-lib
# !wget http://prdownloads.sourceforge.net/ta-lib/ta-lib-0.4.0-src.tar.gz

# !tar -xzf ta-lib-0.4.0-src.tar.gz
# %cd ta-lib/
# !./configure --prefix=$HOME
# !make
# !make install

# !TA_LIBRARY_PATH=~/lib TA_INCLUDE_PATH=~/include pip install ta-lib
# import talib as ta
import matplotlib.pyplot as plt
from collections import Counter
from collections import defaultdict

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 62 kB 18.5 MB/s 
  Attempting uninstall: requests
    Found existing installation: requests 2.23.0
    Uninstalling requests-2.23.0:
      Successfully uninstalled requests-2.23.0


In [ ]:
from collections import Counter
from collections import defaultdict

#####Load Dataset 
***

In [ ]:
#φτιάχνω τη λίστα με τα assets μου -> 50 μετοχές 
#διόρθωση : θα βγάλω τυχαία άλλες 4 μετοχές μαζί με την OGN επειδή δεν έχει το ίδιο μέγεθος με τις άλλες 
#βγάζω OGN ,WRK,HST,CE,ACN
assets= ["ABBV","AEP","AIZ","ALLE","AMAT","AMP","AMZN","AVB","AVY",   
  "AXP","BDX","BF-B","BMY","BR","CARR","CDW","CHTR","CNC",   
  "CNP","COP","CTAS","CZR","DG","DPZ","DRE","DXC","META","FTV",   
  "GOOG","GPC","HIG","JPM","KR","PG","PPL","PRU",   
  "PYPL","RE","ROL","ROST","UNH","URI","V","VRSK","XOM"]
  #άρα πρέπει να κατεβάσουμε όλα τα adj close για όλες τις τιμές όλων των μετοχών και να κάνουμε απόλυτο ranking και σε 5 κλασεις (targets)
r=pd.DataFrame(index=pdr.get_data_yahoo(assets[0],'2021-03-01','2022-07-01')['Adj Close'].index)
#παίρνω τιμές για ένα χρόνο και 3 μήνες
for i in assets:
  # print('i metoxi me onoma:',i,'exei megethos',pdr.get_data_yahoo(i,'2021-01-01','2022-04-01')['Adj Close'].count())
  temp= pdr.get_data_yahoo(i,'2021-03-01','2022-07-01')['Adj Close']
  temp=temp.dropna()
  r[i]=temp.values

[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%********

In [ ]:
#φτιάχνω ένα αντίγραφο με τις τιμές για να το έχω 
rd=pd.DataFrame(r)
rd

ABBV        AEP         AIZ        ALLE        AMAT  \
Date                                                                    
2021-03-01  101.758369  72.935364  123.264771  109.157562  120.793564   
2021-03-02  101.232719  72.688156  123.596611  110.222771  116.100159   
2021-03-03  100.162674  72.564560  124.962944  109.597328  114.064705   
2021-03-04   99.167717  73.448792  125.001999  107.887169  106.950470   
2021-03-05  100.153275  75.017609  128.749710  110.730934  112.098389   
...                ...        ...         ...         ...         ...   
2022-06-24  150.928238  92.870499  172.150925   99.170822   97.111656   
2022-06-27  151.720825  94.239746  172.300293   98.812370   97.361015   
2022-06-28  151.076859  94.338966  172.290344   97.975998   94.777618   
2022-06-29  152.711563  94.626709  170.169083   97.966034   91.705482   
2022-06-30  151.740646  95.192268  172.140961   97.478149   90.747932   

                   AMP        AMZN         AVB         AVY         AXP  ...  \
Date                                                                    ...   
2021-03-01  223.396759  157.307007  169.428787  174.066818  136.349152  ...   
2021-03-02  220.188354  154.726501  170.577332  173.244705  136.879944  ...   
2021-03-03  218.140457  150.250000  173.620926  174.624710  140.163116  ...   
2021-03-04  211.850464  148.878494  170.414627  168.527222  140.251556  ...   
2021-03-05  216.784943  150.022995  170.031738  173.499191  144.822433  ...   
...                ...         ...         ...         ...         ...  ...   
2022-06-24  248.137924  116.459999  193.575409  164.681396  145.605087  ...   
2022-06-27  246.087448  113.220001  197.166199  166.274918  143.752029  ...   
2022-06-28  242.633484  107.400002  195.470001  163.456360  141.659866  ...   
2022-06-29  238.890869  108.919998  195.080002  163.336853  138.949997  ...   
2022-06-30  236.581589  106.209999  194.250000  161.215454  138.619995  ...   

                  PRU        PYPL          RE        ROL        ROST  \
Date                                                                   
2021-03-01  82.900162  273.630005  232.818268  33.455547  118.117958   
2021-03-02  83.274338  269.190002  232.127426  32.895824  115.247551   
2021-03-03  83.601746  255.059998  232.424866  31.874582  108.791573   
2021-03-04  82.853386  239.070007  229.978104  31.324682  109.741852   
2021-03-05  84.808495  239.050003  236.905823  32.345924  110.829277   
...               ...         ...         ...        ...         ...   
2022-06-24  96.279518   77.680000  281.488770  35.017067   77.258453   
2022-06-27  95.824852   75.940002  281.329712  35.186615   76.072624   
2022-06-28  96.546379   71.820000  278.745331  34.418652   72.525093   
2022-06-29  95.212051   71.470001  276.866699  34.877438   71.558487   
2022-06-30  94.569595   69.839996  278.596222  34.827568   69.984024   

                   UNH         URI           V        VRSK        XOM  
Date                                                                   
2021-03-01  326.841492  302.489990  214.501099  165.157501  52.391735  
2021-03-02  326.831787  293.420013  213.649551  164.504959  52.085182  
2021-03-03  325.103027  294.929993  212.738617  162.952637  52.503201  
2021-03-04  326.021088  288.600006  209.421524  159.828247  54.537560  
2021-03-05  339.000946  300.959991  213.293091  166.225327  56.599789  
...                ...         ...         ...         ...        ...  
2022-06-24  494.089691  248.289993  205.146637  172.702087  86.063782  
2022-06-27  504.078339  251.990005  203.200089  173.810226  88.173286  
2022-06-28  506.849640  247.990005  197.769714  168.658813  90.619514  
2022-06-29  514.096924  241.070007  199.147278  171.034866  87.272049  
2022-06-30  512.023376  242.910004  196.541885  172.801910  84.815910  

[338 rows x 45 columns]

In [ ]:
rd1= rd.pct_change().shift(-1)
rd1

ABBV       AEP       AIZ      ALLE      AMAT       AMP  \
Date                                                                     
2021-03-01 -0.005166 -0.003389  0.002692  0.009758 -0.038855 -0.014362   
2021-03-02 -0.010570 -0.001700  0.011055 -0.005674 -0.017532 -0.009301   
2021-03-03 -0.009933  0.012185  0.000313 -0.015604 -0.062370 -0.028835   
2021-03-04  0.009938  0.021359  0.029981  0.026359  0.048134  0.023292   
2021-03-05 -0.005529  0.020152  0.014251  0.028065 -0.068488  0.007962   
...              ...       ...       ...       ...       ...       ...   
2022-06-24  0.005251  0.014744  0.000868 -0.003614  0.002568 -0.008263   
2022-06-27 -0.004244  0.001053 -0.000058 -0.008464 -0.026534 -0.014036   
2022-06-28  0.010820  0.003050 -0.012312 -0.000102 -0.032414 -0.015425   
2022-06-29 -0.006358  0.005977  0.011588 -0.004980 -0.010442 -0.009667   
2022-06-30       NaN       NaN       NaN       NaN       NaN       NaN   

                AMZN       AVB       AVY       AXP  ...       PRU      PYPL  \
Date                                                ...                       
2021-03-01 -0.016404  0.006779 -0.004723  0.003893  ...  0.004514 -0.016226   
2021-03-02 -0.028932  0.017843  0.007966  0.023986  ...  0.003932 -0.052491   
2021-03-03 -0.009128 -0.018467 -0.034918  0.000631  ... -0.008951 -0.062691   
2021-03-04  0.007687 -0.002247  0.029502  0.032591  ...  0.023597 -0.000084   
2021-03-05 -0.016167  0.035238  0.032549  0.019955  ...  0.022722 -0.054215   
...              ...       ...       ...       ...  ...       ...       ...   
2022-06-24 -0.027821  0.018550  0.009676 -0.012727  ... -0.004722 -0.022400   
2022-06-27 -0.051404 -0.008603 -0.016951 -0.014554  ...  0.007530 -0.054253   
2022-06-28  0.014153 -0.001995 -0.000731 -0.019129  ... -0.013821 -0.004873   
2022-06-29 -0.024881 -0.004255 -0.012988 -0.002375  ... -0.006748 -0.022807   
2022-06-30       NaN       NaN       NaN       NaN  ...       NaN       NaN   

                  RE       ROL      ROST       UNH       URI         V  \
Date                                                                     
2021-03-01 -0.002967 -0.016730 -0.024301 -0.000030 -0.029984 -0.003970   
2021-03-02  0.001281 -0.031045 -0.056018 -0.005289  0.005146 -0.004264   
2021-03-03 -0.010527 -0.017252  0.008735  0.002824 -0.021463 -0.015592   
2021-03-04  0.030123  0.032602  0.009909  0.039813  0.042827  0.018487   
2021-03-05  0.016768 -0.013661  0.063997  0.008845  0.005449  0.022562   
...              ...       ...       ...       ...       ...       ...   
2022-06-24 -0.000565  0.004842 -0.015349  0.020216  0.014902 -0.009489   
2022-06-27 -0.009186 -0.021825 -0.046633  0.005498 -0.015874 -0.026724   
2022-06-28 -0.006740  0.013330 -0.013328  0.014299 -0.027904  0.006965   
2022-06-29  0.006247 -0.001430 -0.022002 -0.004033  0.007633 -0.013083   
2022-06-30       NaN       NaN       NaN       NaN       NaN       NaN   

                VRSK       XOM  
Date                            
2021-03-01 -0.003951 -0.005851  
2021-03-02 -0.009436  0.008026  
2021-03-03 -0.019174  0.038747  
2021-03-04  0.040025  0.037813  
2021-03-05  0.020997 -0.000985  
...              ...       ...  
2022-06-24  0.006416  0.024511  
2022-06-27 -0.029638  0.027743  
2022-06-28  0.014088 -0.036940  
2022-06-29  0.010331 -0.028143  
2022-06-30       NaN       NaN  

[338 rows x 45 columns]

In [ ]:
#first: ranks assigned in order they appear in the array
rd2=rd1.rank(axis=1,method='first')
rd2=rd2.dropna()
rd2.astype(int)
jk=rd2.copy()
jk.astype(int)

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-03-01    25   30   39    45     1   12    10   42   26   40  ...   41   
2021-03-02    16   28   36    24    11   18     6   39   33   43  ...   31   
2021-03-03    24   40   32    19     2    6    25   16    5   33  ...   26   
2021-03-04     8   16   28    23    43   19     6    1   27   32  ...   20   
2021-03-05     9   34   28    41     1   22     7   43   42   33  ...   38   
...          ...  ...  ...   ...   ...  ...   ...  ...  ...  ...  ...  ...   
2022-06-23    13    6   15    20    33   31    28    3   43   23  ...   41   
2022-06-24    30   39   20    17    23   10     1   41   36    6  ...   14   
2022-06-27    36   40   39    31    11   23     3   30   17   22  ...   43   
2022-06-28    36   32   12    29     4    8    39   27   28    7  ...   10   
2022-06-29    23   37   44    24    15   16     4   25   12   32  ...   21   

            PYPL  RE  ROL  ROST  UNH  URI   V  VRSK  XOM  
Date                                                      
2021-03-01    11  33    9     4   37    3  28    29   21  
2021-03-02     2  30    4     1   25   32  27    17   34  
2021-03-03     1  23   17    37   34   11  20    12   45  
2021-03-04     3  29   33     7   37   41  13    39   34  
2021-03-05     2  29    8    45   24   19  37    35   13  
...          ...  ..  ...   ...  ...  ...  ..   ...  ...  
2022-06-23    39  30   19    36    1   40  34     5   14  
2022-06-24     2  19   27     5   43   40   8    32   45  
2022-06-27     1  29   15     4   42   20  10     9   44  
2022-06-28    20  16   37    11   41    5  33    38    3  
2022-06-29     6  38   33     7   26   39  11    42    2  

[337 rows x 45 columns]

In [ ]:
def rank_data(df1):
  for i in range(len(df1.index)):
    d=df1.loc[df1.index[i]]  #της κάθε μέρας d[1] δίνει μόνο τις τιμές 
    #print(d)
    d=d.sort_values()
    d[0:9]=1
    d[9:18]=2
    d[18:27]=3
    d[27:36]=4
    d[36:45]=5
    df1.loc[df1.index[i]]=d
    #print(df1.loc[df1.index[i]])
    #print(d)
  df1=df1.astype(int)
  return df1
r5=rd2.copy()
rd3=rank_data(r5)
rd3

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-03-01     3    4    5     5     1    2     2    5    3    5  ...    5   
2021-03-02     2    4    4     3     2    2     1    5    4    5  ...    4   
2021-03-03     3    5    4     3     1    1     3    2    1    4  ...    3   
2021-03-04     1    2    4     3     5    3     1    1    3    4  ...    3   
2021-03-05     1    4    4     5     1    3     1    5    5    4  ...    5   
...          ...  ...  ...   ...   ...  ...   ...  ...  ...  ...  ...  ...   
2022-06-23     2    1    2     3     4    4     4    1    5    3  ...    5   
2022-06-24     4    5    3     2     3    2     1    5    4    1  ...    2   
2022-06-27     4    5    5     4     2    3     1    4    2    3  ...    5   
2022-06-28     4    4    2     4     1    1     5    3    4    1  ...    2   
2022-06-29     3    5    5     3     2    2     1    3    2    4  ...    3   

            PYPL  RE  ROL  ROST  UNH  URI  V  VRSK  XOM  
Date                                                     
2021-03-01     2   4    1     1    5    1  4     4    3  
2021-03-02     1   4    1     1    3    4  3     2    4  
2021-03-03     1   3    2     5    4    2  3     2    5  
2021-03-04     1   4    4     1    5    5  2     5    4  
2021-03-05     1   4    1     5    3    3  5     4    2  
...          ...  ..  ...   ...  ...  ... ..   ...  ...  
2022-06-23     5   4    3     4    1    5  4     1    2  
2022-06-24     1   3    3     1    5    5  1     4    5  
2022-06-27     1   4    2     1    5    3  2     1    5  
2022-06-28     3   2    5     2    5    1  4     5    1  
2022-06-29     1   5    4     1    3    5  2     5    1  

[337 rows x 45 columns]

In [ ]:
rd3.loc[rd3.index=='2022-05-27']

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2022-05-27     2    2    1     2     2    3     5    2    4    4  ...    4   

            PYPL  RE  ROL  ROST  UNH  URI  V  VRSK  XOM  
Date                                                     
2022-05-27     5   3    1     1    1    5  4     1    2  

[1 rows x 45 columns]

#####Functions
***

In [ ]:
def RPS_calculation(hist_data, submission, asset_no=44):
    # print('check')
    if hist_data.shape[0]<=asset_no:
        return np.nan    
    # print('check')
    asset_id = pd.unique(hist_data.symbol)
    
    for i in range(len(pd.unique(hist_data.date))):
        if len(hist_data[hist_data.date == pd.unique(hist_data.date)[i]])<len(asset_id):
            for asset in [x for x in asset_id if x not in hist_data[hist_data.date == pd.unique(hist_data.date)[i]].symbol.values]:
                right_price = hist_data[hist_data.symbol==asset].sort_values(by='date')
                right_price = right_price[right_price.date <= pd.unique(hist_data.date)[i]]
                right_price = right_price.price.iloc[-1]
                hist_data = hist_data.append({'date' : pd.unique(hist_data.date)[i],
                                               'symbol' : asset,
                                               'price' : right_price}, ignore_index=True)

    #Compute percentage returns
    asset_id = sorted(asset_id) 

    #Compute percentage returns
    returns = pd.DataFrame(columns = ["ID", "Return"])
    
    min_date = min(hist_data.date)
    max_date = max(hist_data.date)
    # max_date = np.max(hist_data.date)
    
    for i in range(0,len(asset_id)):
        temp = hist_data.loc[hist_data.symbol==asset_id[i]]
        
        open_price = float(temp.loc[temp.date==min_date].price)
        close_price = float(temp.loc[temp.date==max_date].price)
        
        returns = returns.append({'ID': temp.symbol.iloc[0], 
                                'Return': (close_price - open_price)/open_price}, ignore_index=True)

    #Define the relevant position of each asset
    ranking = pd.DataFrame(columns=["ID", "Position", "Return"])
    ranking.ID = list(asset_id)
    ranking.Return = returns.Return
    ranking.Position = ranking.Return.rank(method = 'min')

    #Handle Ties
    Series_per_position = pd.DataFrame(columns=["Position","Series", "Rank", "Rank1", "Rank2","Rank3", "Rank4", "Rank5"])
    Series_per_position.Position = list(pd.unique(ranking.Position.sort_values(ascending=True)))
    temp = ranking.Position.value_counts()
    temp = pd.DataFrame(zip(temp.index, temp), columns = ["Rank", "Occurencies"])
    temp = temp.sort_values(by = ["Rank"],ascending=True)
    Series_per_position.Series = list(temp.Occurencies)
    Series_per_position

    total_ranks = Series_per_position.Position.values[-1]
    for i in range(0,Series_per_position.shape[0]):
    
        start_p = Series_per_position.Position[i]
        end_p = Series_per_position.Position[i] + Series_per_position.Series[i]
        temp = pd.DataFrame(columns = ["Position","Rank", "Rank1", "Rank2", "Rank3", "Rank4","Rank5"])
        temp.Position = list(range(int(start_p),int(end_p)))

        if(temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))].assign(Rank=1)
            temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))].assign(Rank1=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))].assign(Rank=2)
            temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))].assign(Rank2=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))].assign(Rank=3)
            temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))].assign(Rank3=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))].assign(Rank=4)
            temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))].assign(Rank4=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))].assign(Rank=5)
            temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))].assign(Rank5=1.0)
        temp = temp.fillna(0)
        Series_per_position.iloc[i,2:Series_per_position.shape[1]] = temp.mean(axis = 0).iloc[1:temp.shape[1]]

    Series_per_position = Series_per_position.drop('Series', axis = 1)
    ranking = pd.merge(ranking,Series_per_position, on = "Position")
    ranking = ranking[["ID", "Return", "Position", "Rank", "Rank1", "Rank2", "Rank3", "Rank4", "Rank5"]]
    ranking = ranking.sort_values(["Position"])
    # print(ranking)
    #Evaluate submission
    rps_sub = []
    #for aid in list((pd.unique(ranking.ID))):
    for aid in asset_id:

        target = np.cumsum(ranking.loc[ranking.ID==aid].iloc[:,4:9].values).tolist()
        frc = np.cumsum(submission.loc[submission.ID==aid].iloc[:,1:6].values).tolist()
        rps_sub.append(np.mean([(a - b)**2 for a, b in zip(target, frc)]))
    submission["RPS"] = rps_sub
    
    output = {'RPS' : np.mean(rps_sub),
              'details' : submission}
    
    return(output)

In [ ]:
#Αυτή η συνάρτηση παίρνει τα data και κάνει τη dummy μέτρηση για το διάστημα ενός χρόνου (όσο οριστεί στην ουσία το insample) για μια μετοχή
n=dict() 
def dummy(st,i,p):
  flag=False
  insample=st.iloc[p:-i]
  print('arxi insample',insample.head(1),'kai telos insample',insample.tail(2),'mikos',len(insample))
  if(len(insample)!=60):
    print('---------------------------------------------------------------',flag)
  count=defaultdict(int)
  for word in insample.values:
    count[word]+=1
  print(word,count)
  count=sorted(count.items()) #list Η πρώτη τιμή είναι η κλάση και η δεύτερη πόσες φορές είδα τον αριθμό.
  temp=[]
  for k in range(5):
    flag=True
    for l in count:
      if(l[0]==k+1):
        temp.append(l[1]/len(insample))
        flag=False
        break
    if(flag):
      temp.append(0)
  # print(temp,count)
  data={
      'prediction':temp
  }
  forecast=pd.DataFrame(data)
  return forecast
# #για όλες τις μετοχές υπολογίζεται το counter τους
dummy(rd3['ABBV'],60,248)


arxi insample Date
2022-02-22    5
Name: ABBV, dtype: int64 kai telos insample Date
2022-03-31    3
2022-04-01    2
Name: ABBV, dtype: int64 mikos 29
--------------------------------------------------------------- False
2 defaultdict(<class 'int'>, {5: 4, 1: 2, 3: 8, 2: 7, 4: 8})


prediction
0    0.068966
1    0.241379
2    0.275862
3    0.275862
4    0.137931

In [ ]:
def pred(st,p):
  pred=dict()
  for j in st:
    temp=[]
    date=[]
    for i in range(60,1,-1):
      # print(i)
      date.append(st[j].iloc[-i:-i+1].index.date[0])
      print('imera :',st[j].iloc[-i:-i+1].index.date[0])
      temp.append(dummy(st[j],i,p+(58-i))['prediction'].values)
      # pred[st[j].name]=temp
    #for the last day 
    date.append(st[j].iloc[-1:].index.date[0])
    print('teleutaia imera :',st[j].iloc[-1:].index.date[0])
    temp.append(dummy(st[j],1,p+57)['prediction'].values)
    pred[st[j].name]=temp
  # print(date)
  pred['date']=date
  pred_final=pd.DataFrame.from_dict(pred)
  # pred_final['Date']=date
  # pred_final.set_index('Date')
  # print(pred_final)
  return pred_final
# t=pred(st,p)

In [ ]:
def create_historical(prob):
  prob=prob.rename_axis("symbol", axis="columns")
  prob=prob.T
  prob['date']=prob.columns.date[0]
  prob.columns = ['price', 'date']
  prob=prob.reset_index()
  prob=prob[['symbol','date','price']]
  return prob

In [ ]:
def RPS_data(prob_final,rd):
  RPS=pd.DataFrame()

  # RPS=RPS.drop('date',axis=1)
  # print(RPS.index[2])
  for k in prob_final.index: #for everyday of a stock->index
    prob=pd.DataFrame()
    prob1=pd.DataFrame()
    predic=pd.DataFrame()
    if(prob_final['date'][k]!=prob_final['date'].tail(1).values): #if it's not for the last day 
      #for historical data of two days 
      # prob=rd.loc[(rd.index.date==prob_final['date'][k])]
      # prob1=rd.loc[ (rd.index.date==prob_final['date'][k+1])]

      mask = (rd.loc[(rd.index.date>=prob_final['date'][k])].index)
      prob_table = rd.loc[mask]
      prob = prob_table.shift(-21).head(1)
      print('prob : ',prob)
      mask1 = (rd.loc[(rd.index.date>=prob_final['date'][k+1])].index)
      prob1_table = rd.loc[mask1]
      prob1 = prob1_table.shift(-21).head(1)
      print('prob1 : ',prob1)

      prob=create_historical(prob)
      prob1=create_historical(prob1)
      hist_data=prob.append(prob1)
      print(hist_data)
      predic=prob_final.loc[prob_final['date']==prob_final['date'][k]] #find predictions of this day
      predic=predic.drop('date',axis=1)
      # print(predic)
      data=pd.DataFrame(index=predic.columns)
      data=data.reset_index()
      # print(data)
      data[['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=(0,0,0,0,0)
      for i in range(len(np.array_split(predic.values[0],46))-1):
        data.loc[i,['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=np.array_split(predic.values[0],46)[i][0]
      data.columns = ['ID','Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']
      # print(data)
      #now we have data->predictions and hist_data->historical data so now we can call the RPS
      rps=RPS_calculation(hist_data = hist_data , submission = data)['details']
      # print(rps) ->rps for every stock for one day 
      # print(rps['RPS'])
      tmp=pd.DataFrame(rps['RPS'].values).T
      # print(tmp.T)
      RPS=RPS.append(tmp,ignore_index=True)
      # print(RPS[RPS.index==k])

      
    else:
      #for the last day
      # prob=rd.loc[(rd.index.date==prob_final['date'][k])]
      # prob1=rd.loc[ (rd.index.date==rd.index.date[k+1])]

      # mask = (rd.loc[(rd.index.date>=prob_final['date'][k])].index)
      # prob_table = rd.loc[mask]
      # prob = prob_table.head(1)
      # print('prob teleutaio :', prob)
      # prob1 = pd.DataFrame(prob_table.iloc[1]).T
      # print('prob1 teleutaio',prob1)

      mask = (rd.loc[(rd.index.date>=prob_final['date'][k])].index)
      prob_table = rd.loc[mask]
      prob = prob_table.shift(-21).head(1)
      print('prob teleutaio :', prob)
      prob1 = pd.DataFrame(prob_table.iloc[1]).T
      print('prob1 : ',prob1)
      
      prob=create_historical(prob)
      prob1=create_historical(prob1)
      hist_data=prob.append(prob1)
      print(hist_data)
      predic=prob_final.loc[prob_final['date']==prob_final['date'][k]] #find predictions of this day
      predic=predic.drop('date',axis=1)
      # print(predic)
      data=pd.DataFrame(index=predic.columns)
      data=data.reset_index()
      # print(data)
      data[['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=(0,0,0,0,0)
      for i in range(len(np.array_split(predic.values[0],46))-1):
        data.loc[i,['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=np.array_split(predic.values[0],46)[i][0]
      data.columns = ['ID','Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']
      # print(data)

      #now we have data->predictions and hist_data->historical data so now we can call the RPS
      rps=RPS_calculation(hist_data = hist_data , submission = data)['details']
      # print(rps) ->rps for every stock for one day 
      # print(rps['RPS'])
      tmp=pd.DataFrame(rps['RPS'].values).T
      # print(tmp.T)
      RPS=RPS.append(tmp,ignore_index=True)              
  return RPS

In [ ]:
def create_RPS(prob_final,RPS):
  d=prob_final['date']
  name=prob_final.columns[:-1]
  # print(np.split(name.values,len(name)))
  # print(d.values)
  RPS['date']=d.values
  RPS=RPS.set_index('date')
  RPS.columns=assets
  return RPS

####**For 6 Mar.-1 Apr.** 

#####Prepare the dataset  

In [ ]:
#cut the dataset(with the ranks) we have until 6 March 
q1_1=rd3.copy()
q1_1=q1_1.loc[(q1_1.index<='2022-03-04')]
q1_1

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-03-01     3    4    5     5     1    2     2    5    3    5  ...    5   
2021-03-02     2    4    4     3     2    2     1    5    4    5  ...    4   
2021-03-03     3    5    4     3     1    1     3    2    1    4  ...    3   
2021-03-04     1    2    4     3     5    3     1    1    3    4  ...    3   
2021-03-05     1    4    4     5     1    3     1    5    5    4  ...    5   
...          ...  ...  ...   ...   ...  ...   ...  ...  ...  ...  ...  ...   
2022-02-28     4    4    2     5     2    1     3    3    1    1  ...    1   
2022-03-01     2    2    3     4     4    5     2    4    4    2  ...    5   
2022-03-02     4    5    5     4     1    3     1    5    2    3  ...    3   
2022-03-03     3    5    3     3     1    1     3    4    2    1  ...    2   
2022-03-04     4    5    5     3     2    1     1    4    1    1  ...    2   

            PYPL  RE  ROL  ROST  UNH  URI  V  VRSK  XOM  
Date                                                     
2021-03-01     2   4    1     1    5    1  4     4    3  
2021-03-02     1   4    1     1    3    4  3     2    4  
2021-03-03     1   3    2     5    4    2  3     2    5  
2021-03-04     1   4    4     1    5    5  2     5    4  
2021-03-05     1   4    1     5    3    3  5     4    2  
...          ...  ..  ...   ...  ...  ... ..   ...  ...  
2022-02-28     1   1    5     2    5    2  2     5    5  
2022-03-01     1   4    4     5    3    5  1     2    3  
2022-03-02     1   2    1     2    4    4  2     4    4  
2022-03-03     3   2    4     1    5    1  1     5    5  
2022-03-04     1   1    5     2    3    1  2     5    5  

[257 rows x 45 columns]

In [ ]:
# not needed anymore
# March '21
#save the values of the month
# march_21 = rd3.loc[(rd3.index < '2021-04-02') & (rd3.index > '2021-03-04')]
# march_21

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-03-05     1    4    4     5     1    3     1    5    5    4  ...    5   
2021-03-08     4    3    4     1     5    3     5    2    2    1  ...    1   
2021-03-09     3    2    5     4     1    3     1    4    1    3  ...    4   
2021-03-10     3    1    1     1     5    3     5    4    2    4  ...    2   
2021-03-11     3    4    2     5     1    2     1    5    3    3  ...    5   
2021-03-12     5    4    4     3     2    3     1    4    5    1  ...    2   
2021-03-15     4    5    3     5     5    1     4    2    2    1  ...    1   
2021-03-16     1    1    4     4     5    5     5    3    3    4  ...    5   
2021-03-17     2    4    5     3     1    4     1    3    4    2  ...    3   
2021-03-18     3    5    4     1     4    4     5    1    2    2  ...    2   
2021-03-19     5    2    1     3     5    2     4    4    3    2  ...    1   
2021-03-22     2    5    4     3     1    1     5    4    2    1  ...    1   
2021-03-23     1    4    4     5     5    3     1    3    3    5  ...    4   
2021-03-24     3    1    3     4     1    4     1    4    5    5  ...    5   
2021-03-25     4    1    2     4     5    4     1    2    2    2  ...    2   
2021-03-26     4    4    3     3     1    2     4    2    2    2  ...    2   
2021-03-29     3    1    4     2     4    5     2    4    5    4  ...    5   
2021-03-30     5    4    1     4     5    3     5    1    3    2  ...    2   
2021-03-31     2    3    2     4     5    3     4    3    5    5  ...    4   
2021-04-01     1    2    2     5     3    3     5    1    4    3  ...    2   

            PYPL  RE  ROL  ROST  UNH  URI  V  VRSK  XOM  
Date                                                     
2021-03-05     1   4    1     5    3    3  5     4    2  
2021-03-08     5   1    4     5    4    1  3     5    1  
2021-03-09     1   3    3     1    1    5  3     2    5  
2021-03-10     5   3    3     2    4    5  4     1    2  
2021-03-11     1   4    2     4    4    5  1     1    4  
2021-03-12     2   4    5     5    1    5  1     4    1  
2021-03-15     3   3    2     2    4    1  4     3    2  
2021-03-16     4   2    1     3    2    5  2     2    4  
2021-03-17     1   4    5     3    5    3  3     3    1  
2021-03-18     5   1    5     1    4    2  1     4    2  
2021-03-19     4   2    5     2    3    1  3     5    1  
2021-03-22     4   2    2     1    4    1  4     5    2  
2021-03-23     1   4    2     1    4    5  3     2    5  
2021-03-24     2   4    2     5    2    5  2     1    1  
2021-03-25     5   2    2     5    3    5  4     4    4  
2021-03-26     1   5    3     1    4    1  3     4    3  
2021-03-29     4   3    2     4    1    5  1     1    1  
2021-03-30     5   1    5     3    3    2  3     4    1  
2021-03-31     4   3    3     2    1    2  5     4    5  
2021-04-01     4   1    4     5    2    1  3     3    1  

[20 rows x 45 columns]

In [ ]:
#March 22
# march_22 = rd3.loc[(rd3.index > '2022-03-04') & (rd3.index <= '2022-04-01')]
# march_22

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2022-03-07     2    2    3     1     5    3     3    2    4    4  ...    5   
2022-03-08     2    1    3     4     4    5     3    3    5    5  ...    4   
2022-03-09     4    4    4     1     1    3     5    3    2    4  ...    3   
2022-03-10     5    4    5     2     3    4     3    3    4    3  ...    5   
2022-03-11     5    2    3     3     1    3     1    2    5    5  ...    5   
2022-03-14     4    2    3     4     5    4     5    1    1    3  ...    1   
2022-03-15     2    1    2     3     5    5     4    2    3    3  ...    4   
2022-03-16     4    1    3     3     3    4     5    3    1    5  ...    3   
2022-03-17     3    1    2     2     5    3     5    1    2    5  ...    1   
2022-03-18     4    4    5     2     2    2     4    3    3    2  ...    5   
2022-03-21     2    3    4     3     4    5     5    1    2    4  ...    5   
2022-03-22     3    5    4     1     1    3     3    4    1    1  ...    2   
2022-03-23     3    2    5     1     5    5     1    3    4    4  ...    4   
2022-03-24     3    2    3     1     1    4     3    5    5    3  ...    5   
2022-03-25     3    3    1     4     3    1     5    4    3    2  ...    1   
2022-03-28     1    3    1     3     4    2     1    5    5    2  ...    2   
2022-03-29     5    5    4     2     1    3     1    1    2    3  ...    3   
2022-03-30     4    5    5     1     1    1     2    3    3    3  ...    3   
2022-03-31     3    5    5     4     1    1     2    5    3    2  ...    2   
2022-04-01     2    2    1     3     4    3     5    1    2    4  ...    1   

            PYPL  RE  ROL  ROST  UNH  URI  V  VRSK  XOM  
Date                                                     
2022-03-07     5   4    1     5    1    5  4     3    4  
2022-03-08     5   4    1     4    3    3  5     2    1  
2022-03-09     1   3    3     5    5    5  2     2    5  
2022-03-10     1   3    2     1    2    5  4     2    4  
2022-03-11     3   3    5     1    4    2  5     5    1  
2022-03-14     5   5    1     3    3    4  5     4    1  
2022-03-15     5   3    2     5    1    4  4     3    1  
2022-03-16     5   2    4     2    4    5  2     5    5  
2022-03-17     5   3    1     4    1    1  5     5    1  
2022-03-18     1   4    1     1    4    4  2     5    5  
2022-03-21     5   4    1     3    1    5  3     3    1  
2022-03-22     1   5    4     2    4    4  2     2    5  
2022-03-23     3   3    2     3    5    4  3     2    2  
2022-03-24     1   5    3     1    1    4  3     1    5  
2022-03-25     5   2    5     5    2    2  4     5    1  
2022-03-28     5   3    4     5    1    2  5     3    1  
2022-03-29     1   5    5     1    5    2  1     5    5  
2022-03-30     1   4    4     2    2    3  4     4    3  
2022-03-31     3   5    1     2    3    2  5     2    3  
2022-04-01     5   1    4     5    2    1  4     4    3  

[20 rows x 45 columns]

In [ ]:
#not needed anymore (no dummy data)
# for i in march_22:
#   march_22[i] = march_21[i].values
# march_22

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2022-03-07     1    4    4     5     1    3     1    5    5    4  ...    5   
2022-03-08     4    3    4     1     5    3     5    2    2    1  ...    1   
2022-03-09     3    2    5     4     1    3     1    4    1    3  ...    4   
2022-03-10     3    1    1     1     5    3     5    4    2    4  ...    2   
2022-03-11     3    4    2     5     1    2     1    5    3    3  ...    5   
2022-03-14     5    4    4     3     2    3     1    4    5    1  ...    2   
2022-03-15     4    5    3     5     5    1     4    2    2    1  ...    1   
2022-03-16     1    1    4     4     5    5     5    3    3    4  ...    5   
2022-03-17     2    4    5     3     1    4     1    3    4    2  ...    3   
2022-03-18     3    5    4     1     4    4     5    1    2    2  ...    2   
2022-03-21     5    2    1     3     5    2     4    4    3    2  ...    1   
2022-03-22     2    5    4     3     1    1     5    4    2    1  ...    1   
2022-03-23     1    4    4     5     5    3     1    3    3    5  ...    4   
2022-03-24     3    1    3     4     1    4     1    4    5    5  ...    5   
2022-03-25     4    1    2     4     5    4     1    2    2    2  ...    2   
2022-03-28     4    4    3     3     1    2     4    2    2    2  ...    2   
2022-03-29     3    1    4     2     4    5     2    4    5    4  ...    5   
2022-03-30     5    4    1     4     5    3     5    1    3    2  ...    2   
2022-03-31     2    3    2     4     5    3     4    3    5    5  ...    4   
2022-04-01     1    2    2     5     3    3     5    1    4    3  ...    2   

            PYPL  RE  ROL  ROST  UNH  URI  V  VRSK  XOM  
Date                                                     
2022-03-07     1   4    1     5    3    3  5     4    2  
2022-03-08     5   1    4     5    4    1  3     5    1  
2022-03-09     1   3    3     1    1    5  3     2    5  
2022-03-10     5   3    3     2    4    5  4     1    2  
2022-03-11     1   4    2     4    4    5  1     1    4  
2022-03-14     2   4    5     5    1    5  1     4    1  
2022-03-15     3   3    2     2    4    1  4     3    2  
2022-03-16     4   2    1     3    2    5  2     2    4  
2022-03-17     1   4    5     3    5    3  3     3    1  
2022-03-18     5   1    5     1    4    2  1     4    2  
2022-03-21     4   2    5     2    3    1  3     5    1  
2022-03-22     4   2    2     1    4    1  4     5    2  
2022-03-23     1   4    2     1    4    5  3     2    5  
2022-03-24     2   4    2     5    2    5  2     1    1  
2022-03-25     5   2    2     5    3    5  4     4    4  
2022-03-28     1   5    3     1    4    1  3     4    3  
2022-03-29     4   3    2     4    1    5  1     1    1  
2022-03-30     5   1    5     3    3    2  3     4    1  
2022-03-31     4   3    3     2    1    2  5     4    5  
2022-04-01     4   1    4     5    2    1  3     3    1  

[20 rows x 45 columns]

In [ ]:
#now that we have the new "dummy" month all we have to do is to join it with the original dataframe
# q1_1 = pd.concat([q1_1,march_22])
# q1_1

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-04-05     2    4    4     5     1    2     3    4    5    3  ...    4   
2021-04-06     2    2    5     2     2    4     5    4    1    4  ...    5   
2021-04-07     5    2    3     2     3    2     4    1    5    3  ...    1   
2021-04-08     4    1    4     3     1    5     5    2    5    2  ...    5   
2021-04-09     4    3    4     2     1    5     3    4    2    2  ...    5   
...          ...  ...  ...   ...   ...  ...   ...  ...  ...  ...  ...  ...   
2022-03-28     4    4    3     3     1    2     4    2    2    2  ...    2   
2022-03-29     3    1    4     2     4    5     2    4    5    4  ...    5   
2022-03-30     5    4    1     4     5    3     5    1    3    2  ...    2   
2022-03-31     2    3    2     4     5    3     4    3    5    5  ...    4   
2022-04-01     1    2    2     5     3    3     5    1    4    3  ...    2   

            PYPL  RE  ROL  ROST  UNH  URI  V  VRSK  XOM  
Date                                                     
2021-04-05     5   5    3     4    1    1  3     2    2  
2021-04-06     5   5    1     3    3    1  3     1    4  
2021-04-07     5   2    5     5    3    3  4     4    1  
2021-04-08     3   3    4     3    5    4  3     3    1  
2021-04-09     5   3    4     2    3    5  1     2    1  
...          ...  ..  ...   ...  ...  ... ..   ...  ...  
2022-03-28     1   5    3     1    4    1  3     4    3  
2022-03-29     4   3    2     4    1    5  1     1    1  
2022-03-30     5   1    5     3    3    2  3     4    1  
2022-03-31     4   3    3     2    1    2  5     4    5  
2022-04-01     4   1    4     5    2    1  3     3    1  

[253 rows x 45 columns]

#####15 days
***

In [ ]:
t_15d=pred(q1_1,184)
t_15d=pd.DataFrame.from_dict(t_15d)
t_15d.set_index('date')
RPS_15d= RPS_data(t_15d,rd)
RPS_15d= create_RPS(t_15d,RPS_15d)
RPS_15d
print(RPS_15d.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-01-06    2
Name: UNH, dtype: int64 kai telos insample Date
2022-01-26    4
2022-01-27    2
Name: UNH, dtype: int64 mikos 15
2 defaultdict(<class 'int'>, {2: 3, 5: 3, 3: 4, 4: 5})
imera : 2022-01-31
arxi insample Date
2022-01-07    5
Name: UNH, dtype: int64 kai telos insample Date
2022-01-27    2
2022-01-28    3
Name: UNH, dtype: int64 mikos 15
3 defaultdict(<class 'int'>, {5: 3, 3: 5, 2: 2, 4: 5})
imera : 2022-02-01
arxi insample Date
2022-01-10    3
Name: UNH, dtype: int64 kai telos insample Date
2022-01-28    3
2022-01-31    1
Name: UNH, dtype: int64 mikos 15
1 defaultdict(<class 'int'>, {3: 5, 5: 2, 2: 2, 4: 5, 1: 1})
imera : 2022-02-02
arxi insample Date
2022-01-11    5
Name: UNH, dtype: int64 kai telos insample Date
2022-01-31    1
2022-02-01    5
Name: UNH, dtype: int64 mikos 15
5 defaultdict(<class 'int'>, {5: 3, 2: 2, 4: 5, 3: 4, 1: 1})
imera : 2022-02-03
arxi insample Date
2022-01-12    2
Name: UNH, dtype: int64 kai t

In [ ]:
RPS_15d

ABBV       AEP       AIZ      ALLE      AMAT       AMP  \
date                                                                     
2021-12-08  0.157333  0.044444  0.248000  0.130667  0.140444  0.077333   
2021-12-09  0.197333  0.325333  0.034667  0.130667  0.140444  0.286222   
2021-12-10  0.100444  0.106667  0.088889  0.112889  0.282667  0.158222   
2021-12-13  0.382222  0.277333  0.084444  0.112889  0.109333  0.158222   
2021-12-14  0.090667  0.104000  0.040889  0.112889  0.246222  0.178667   
2021-12-15  0.090667  0.083556  0.058667  0.098667  0.225778  0.229333   
2021-12-16  0.282667  0.064000  0.040889  0.070222  0.182222  0.244444   
2021-12-17  0.264000  0.079111  0.065778  0.232889  0.233778  0.045333   
2021-12-20  0.078222  0.188444  0.048000  0.292444  0.132444  0.244444   
2021-12-21  0.268444  0.353778  0.197333  0.276444  0.192000  0.057778   
2021-12-22  0.095111  0.080000  0.197333  0.103111  0.225778  0.072000   
2021-12-23  0.078222  0.082667  0.410667  0.062222  0.176000  0.138667   
2021-12-27  0.101333  0.101333  0.185778  0.062222  0.305778  0.202667   
2021-12-28  0.115556  0.144000  0.083556  0.223111  0.125333  0.285333   
2021-12-29  0.445333  0.162667  0.061333  0.061333  0.152000  0.132444   
2021-12-30  0.302222  0.322667  0.082667  0.248000  0.143111  0.136889   
2021-12-31  0.129778  0.069333  0.070222  0.132444  0.121778  0.136889   
2022-01-03  0.129778  0.202667  0.105778  0.240000  0.218667  0.120000   
2022-01-04  0.080889  0.151111  0.090667  0.224889  0.152000  0.101333   
2022-01-05  0.147556  0.104000  0.090667  0.104889  0.141333  0.181333   
2022-01-06  0.147556  0.122667  0.076444  0.109333  0.141333  0.095111   
2022-01-07  0.309333  0.128889  0.214222  0.271111  0.154667  0.110222   
2022-01-10  0.168889  0.128889  0.148444  0.211556  0.221333  0.190222   
2022-01-11  0.119111  0.275556  0.205333  0.098667  0.221333  0.360889   
2022-01-12  0.201778  0.269333  0.080000  0.112000  0.141333  0.208000   
2022-01-13  0.063111  0.304000  0.226667  0.245333  0.208000  0.190222   
2022-01-14  0.229333  0.186667  0.216889  0.222222  0.208000  0.190222   
2022-01-18  0.127111  0.155556  0.062222  0.155556  0.118222  0.292444   
2022-01-19  0.127111  0.056000  0.062222  0.101333  0.158222  0.212444   
2022-01-20  0.222222  0.164444  0.098667  0.112000  0.115556  0.097778   
2022-01-21  0.240889  0.090667  0.115556  0.185778  0.157333  0.097778   
2022-01-24  0.267556  0.057778  0.046222  0.172444  0.264889  0.211556   
2022-01-25  0.098667  0.048000  0.112889  0.168000  0.102222  0.209778   
2022-01-26  0.148444  0.133333  0.262222  0.093333  0.118222  0.073778   
2022-01-27  0.121778  0.033778  0.093333  0.318222  0.118222  0.316444   
2022-01-28  0.165333  0.247111  0.043556  0.171556  0.207111  0.235556   
2022-01-31  0.124444  0.190222  0.337778  0.158222  0.186667  0.075556   
2022-02-01  0.101333  0.202667  0.041778  0.069333  0.200000  0.275556   
2022-02-02  0.129778  0.182222  0.335111  0.076444  0.133333  0.272889   
2022-02-03  0.151111  0.226667  0.038222  0.162667  0.275556  0.080889   
2022-02-04  0.178667  0.331556  0.038222  0.173333  0.168889  0.267556   
2022-02-07  0.098667  0.051556  0.104889  0.209778  0.176000  0.083556   
2022-02-08  0.178667  0.071111  0.261333  0.108444  0.086222  0.082667   
2022-02-09  0.181333  0.120889  0.062222  0.082667  0.274667  0.058667   
2022-02-10  0.101333  0.094222  0.062222  0.149333  0.194667  0.063111   
2022-02-11  0.181333  0.240889  0.173333  0.068444  0.200889  0.183111   
2022-02-14  0.093333  0.240889  0.080000  0.057778  0.076444  0.069333   
2022-02-15  0.106667  0.195556  0.179556  0.105778  0.186667  0.104000   
2022-02-16  0.093333  0.189333  0.166222  0.100444  0.173333  0.205333   
2022-02-17  0.190222  0.127111  0.054222  0.093333  0.088889  0.181333   
2022-02-18  0.104889  0.280000  0.054222  0.178667  0.274667  0.112000   
2022-02-22  0.119111  0.109333  0.133333  0.178667  0.246222  0.150222   
2022-02-23  0.141333

In [ ]:
RPS_15d.mean(axis=1)

date
2021-12-08    0.147081
2021-12-09    0.182360
2021-12-10    0.159328
2021-12-13    0.167427
2021-12-14    0.150163
2021-12-15    0.149531
2021-12-16    0.148069
2021-12-17    0.160237
2021-12-20    0.148148
2021-12-21    0.187417
2021-12-22    0.158736
2021-12-23    0.161975
2021-12-27    0.156642
2021-12-28    0.166479
2021-12-29    0.173630
2021-12-30    0.191881
2021-12-31    0.158301
2022-01-03    0.155457
2022-01-04    0.172326
2022-01-05    0.167467
2022-01-06    0.164188
2022-01-07    0.169719
2022-01-10    0.153837
2022-01-11    0.158143
2022-01-12    0.185284
2022-01-13    0.167032
2022-01-14    0.163793
2022-01-18    0.128395
2022-01-19    0.167230
2022-01-20    0.157590
2022-01-21    0.140128
2022-01-24    0.214123
2022-01-25    0.146647
2022-01-26    0.165412
2022-01-27    0.165965
2022-01-28    0.183743
2022-01-31    0.157748
2022-02-01    0.154035
2022-02-02    0.150953
2022-02-03    0.174736
2022-02-04    0.180267
2022-02-07    0.151348
2022-02-08    0.158183
2022-0

In [ ]:
RPS_15d.mean(axis=1).mean()

0.1643146502057613

#####One Month (20 working days)
***

In [ ]:
t_1m=pred(q1_1,179)
t_1m=pd.DataFrame.from_dict(t_1m)
t_1m.set_index('date')
RPS_1m= RPS_data(t_1m,rd)
RPS_1m= create_RPS(t_1m,RPS_1m)
RPS_1m
print(RPS_1m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-01-26    4
Name: UNH, dtype: int64 mikos 20
4 defaultdict(<class 'int'>, {3: 6, 2: 3, 1: 2, 4: 6, 5: 3})
imera : 2022-01-28
arxi insample Date
2021-12-30    2
Name: UNH, dtype: int64 kai telos insample Date
2022-01-26    4
2022-01-27    2
Name: UNH, dtype: int64 mikos 20
2 defaultdict(<class 'int'>, {2: 4, 3: 5, 1: 2, 4: 6, 5: 3})
imera : 2022-01-31
arxi insample Date
2021-12-31    3
Name: UNH, dtype: int64 kai telos insample Date
2022-01-27    2
2022-01-28    3
Name: UNH, dtype: int64 mikos 20
3 defaultdict(<class 'int'>, {3: 6, 1: 2, 4: 6, 2: 3, 5: 3})
imera : 2022-02-01
arxi insample Date
2022-01-03    1
Name: UNH, dtype: int64 kai telos insample Date
2022-01-28    3
2022-01-31    1
Name: UNH, dtype: int64 mikos 20
1 defaultdict(<class 'int'>, {1: 3, 4: 6, 2: 3, 5: 3, 3: 5})
imera : 2022-02-02
arxi insample Date
2022-01-04    4
Name: UNH, dtype: int64 kai telos insample Date
2022-01-31    1
2022-02-01    5
Name: UNH, dtype:

In [ ]:
RPS_1m

ABBV     AEP     AIZ    ALLE    AMAT     AMP    AMZN     AVB  \
date                                                                         
2021-12-08  0.1900  0.0635  0.2470  0.1420  0.1615  0.0630  0.0975  0.1025   
2021-12-09  0.1500  0.2725  0.0450  0.1095  0.1415  0.2915  0.2550  0.1310   
2021-12-10  0.0850  0.1110  0.0895  0.1295  0.2350  0.1450  0.0975  0.1110   
2021-12-13  0.3490  0.2125  0.1020  0.1185  0.1190  0.1545  0.2205  0.0985   
2021-12-14  0.1225  0.0890  0.0355  0.1140  0.2495  0.1450  0.1750  0.1155   
2021-12-15  0.0990  0.0765  0.0410  0.1250  0.1895  0.2275  0.0850  0.0930   
2021-12-16  0.2505  0.0730  0.0375  0.0650  0.1895  0.2565  0.1935  0.1310   
2021-12-17  0.2505  0.0730  0.0850  0.2250  0.1895  0.0510  0.1935  0.1110   
2021-12-20  0.0715  0.2130  0.0510  0.3180  0.1430  0.2335  0.1935  0.1025   
2021-12-21  0.2575  0.3295  0.2105  0.3095  0.1850  0.0570  0.1795  0.2705   
2021-12-22  0.0975  0.0895  0.2200  0.1050  0.2555  0.0670  0.2300  0.2105   
2021-12-23  0.0910  0.0910  0.4165  0.0725  0.1820  0.1260  0.0830  0.0895   
2021-12-27  0.0975  0.1090  0.1870  0.0725  0.3080  0.2045  0.1980  0.1515   
2021-12-28  0.1375  0.1400  0.0565  0.2550  0.1020  0.2735  0.3135  0.0915   
2021-12-29  0.3890  0.1400  0.0600  0.0770  0.1590  0.1290  0.3625  0.1515   
2021-12-30  0.2490  0.3085  0.0750  0.2740  0.1150  0.1410  0.2110  0.1710   
2021-12-31  0.1265  0.0830  0.0610  0.1340  0.1295  0.1640  0.0710  0.2110   
2022-01-03  0.1265  0.2310  0.1275  0.2365  0.1665  0.0975  0.1685  0.0805   
2022-01-04  0.0795  0.1510  0.1150  0.2565  0.1320  0.1210  0.3150  0.1855   
2022-01-05  0.1125  0.0785  0.0750  0.1130  0.1500  0.2365  0.0870  0.3375   
2022-01-06  0.2170  0.1630  0.0950  0.0775  0.1470  0.0775  0.3470  0.3245   
2022-01-07  0.3780  0.1770  0.2565  0.2775  0.1870  0.0805  0.1575  0.2245   
2022-01-10  0.1380  0.1675  0.1165  0.2070  0.2270  0.2005  0.0710  0.3150   
2022-01-11  0.0930  0.2070  0.2565  0.0945  0.2625  0.3300  0.1905  0.0895   
2022-01-12  0.1770  0.2870  0.1050  0.0945  0.1510  0.2015  0.2990  0.1710   
2022-01-13  0.0710  0.2870  0.2635  0.2050  0.1805  0.1770  0.0870  0.1710   
2022-01-14  0.1965  0.1470  0.2635  0.1890  0.1455  0.1695  0.3155  0.1860   
2022-01-18  0.1115  0.1955  0.0950  0.1415  0.1605  0.3185  0.0780  0.0460   
2022-01-19  0.1240  0.0910  0.0675  0.0885  0.2070  0.1785  0.1350  0.0495   
2022-01-20  0.2025  0.1925  0.1065  0.1015  0.1690  0.1025  0.1140  0.2495   
2022-01-21  0.2170  0.0830  0.0990  0.2430  0.1605  0.0995  0.0950  0.0695   
2022-01-24  0.2780  0.0630  0.0610  0.1275  0.2605  0.1490  0.3785  0.0495   
2022-01-25  0.0910  0.0510  0.0650  0.1495  0.1075  0.2595  0.1185  0.0710   
2022-01-26  0.1375  0.1665  0.2075  0.0975  0.1205  0.0780  0.2340  0.3510   
2022-01-27  0.1250  0.0390  0.1450  0.3075  0.1075  0.3055  0.0995  0.0455   
2022-01-28  0.1290  0.2100  0.0565  0.1710  0.2065  0.2055  0.0875  0.0855   
2022-01-31  0.1305  0.1745  0.2730  0.1830  0.1690  0.0925  0.1805  0.2835   
2022-02-01  0.0990  0.1825  0.0540  0.0830  0.1550  0.3325  0.0970  0.1100   
2022-02-02  0.1305  0.1750  0.3085  0.0900  0.1245  0.3300  0.1915  0.1115   
2022-02-03  0.1305  0.1950  0.0485  0.1545  0.2380  0.0830  0.1075  0.1190   
2022-02-04  0.1515  0.3350  0.0465  0.1855  0.1650  0.2230  0.1080  0.0665   
2022-02-07  0.1085  0.0515  0.1395  0.2005  0.2175  0.0855  0.2680  0.0680   
2022-02-08  0.1790  0.0580  0.2970  0.0910  0.0975  0.0655  0.1115  0.0790   
2022-02-09  0.1815  0.1755  0.0450  0.0745  0.2430  0.0725  0.1745  0.1215   
2022-02-10  0.1185  0.1505  0.0450  0.1590  0.2430  0.0750  0.2650  0.2250   
2022-02-11  0.1790  0.3105  0.1495  0.0705  0.2495  0.2355  0.1450  0.1050   
2022-02-14  0.0990  0.2700  0.0580  0.0630  0.0975  0.1135  0.2495  0.0945   
2022-02-15  0.1010  0.2325  0.1710  0.1105  0.2345  0.0745  0.2495  0.1975   
2022-02-16  0.0925  0.1335  0.1660  0.1055  0.1555  0.1795  0.1285  0.0975   
2022-02-17  0.2185  0.1170  0.0530  

In [ ]:
RPS_1m.mean(axis=1).mean()

0.1634496296296296

In [ ]:
RPS_1m.mean(axis=1)

date
2021-12-08    0.154000
2021-12-09    0.177533
2021-12-10    0.163800
2021-12-13    0.170511
2021-12-14    0.151889
2021-12-15    0.146533
2021-12-16    0.148067
2021-12-17    0.159311
2021-12-20    0.151889
2021-12-21    0.188111
2021-12-22    0.164444
2021-12-23    0.161311
2021-12-27    0.161244
2021-12-28    0.170289
2021-12-29    0.169689
2021-12-30    0.182022
2021-12-31    0.154800
2022-01-03    0.154156
2022-01-04    0.177067
2022-01-05    0.168733
2022-01-06    0.166533
2022-01-07    0.176622
2022-01-10    0.152978
2022-01-11    0.148978
2022-01-12    0.175578
2022-01-13    0.165067
2022-01-14    0.151711
2022-01-18    0.138867
2022-01-19    0.160089
2022-01-20    0.158667
2022-01-21    0.145689
2022-01-24    0.200111
2022-01-25    0.144644
2022-01-26    0.164622
2022-01-27    0.168867
2022-01-28    0.170356
2022-01-31    0.157244
2022-02-01    0.157178
2022-02-02    0.154711
2022-02-03    0.166933
2022-02-04    0.179089
2022-02-07    0.151378
2022-02-08    0.151889
2022-0

#####Two months
***

In [ ]:
t_2m=pred(q1_1,159)
t_2m=pd.DataFrame.from_dict(t_2m)
t_2m.set_index('date')
RPS_2m= RPS_data(t_2m,rd)
RPS_2m= create_RPS(t_2m,RPS_2m)
RPS_2m
print(RPS_2m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-01-26    4
Name: UNH, dtype: int64 mikos 40
4 defaultdict(<class 'int'>, {4: 15, 1: 3, 3: 9, 5: 7, 2: 6})
imera : 2022-01-28
arxi insample Date
2021-12-01    1
Name: UNH, dtype: int64 kai telos insample Date
2022-01-26    4
2022-01-27    2
Name: UNH, dtype: int64 mikos 40
2 defaultdict(<class 'int'>, {1: 3, 4: 14, 3: 9, 5: 7, 2: 7})
imera : 2022-01-31
arxi insample Date
2021-12-02    4
Name: UNH, dtype: int64 kai telos insample Date
2022-01-27    2
2022-01-28    3
Name: UNH, dtype: int64 mikos 40
3 defaultdict(<class 'int'>, {4: 14, 3: 10, 5: 7, 2: 7, 1: 2})
imera : 2022-02-01
arxi insample Date
2021-12-03    4
Name: UNH, dtype: int64 kai telos insample Date
2022-01-28    3
2022-01-31    1
Name: UNH, dtype: int64 mikos 40
1 defaultdict(<class 'int'>, {4: 13, 3: 10, 5: 7, 2: 7, 1: 3})
imera : 2022-02-02
arxi insample Date
2021-12-06    3
Name: UNH, dtype: int64 kai telos insample Date
2022-01-31    1
2022-02-01    5
Name: UNH, 

In [ ]:
RPS_2m

ABBV       AEP       AIZ      ALLE      AMAT       AMP  \
date                                                                     
2021-12-08  0.239750  0.057875  0.202500  0.147875  0.207875  0.070125   
2021-12-09  0.121875  0.243125  0.060250  0.096625  0.113625  0.240125   
2021-12-10  0.078375  0.121250  0.074375  0.131750  0.157750  0.095750   
2021-12-13  0.282500  0.250125  0.079750  0.125750  0.180375  0.104125   
2021-12-14  0.185000  0.100875  0.059750  0.115500  0.166500  0.100500   
2021-12-15  0.169375  0.102500  0.066500  0.109250  0.270375  0.280500   
2021-12-16  0.164250  0.102500  0.066500  0.079250  0.270375  0.276625   
2021-12-17  0.159375  0.108875  0.071375  0.239250  0.286250  0.053250   
2021-12-20  0.094500  0.224375  0.071375  0.280250  0.192125  0.264125   
2021-12-21  0.174500  0.294375  0.166750  0.274000  0.138500  0.058875   
2021-12-22  0.154500  0.107250  0.164875  0.114000  0.312750  0.064125   
2021-12-23  0.149625  0.116250  0.347375  0.074250  0.132750  0.104125   
2021-12-27  0.154500  0.119625  0.189750  0.075000  0.312750  0.252750   
2021-12-28  0.089375  0.125125  0.065125  0.256125  0.132875  0.257750   
2021-12-29  0.331125  0.125125  0.072625  0.077500  0.142875  0.117750   
2021-12-30  0.171125  0.269000  0.075250  0.246750  0.129625  0.129875   
2021-12-31  0.089375  0.105625  0.065250  0.137250  0.128125  0.140875   
2022-01-03  0.166250  0.221125  0.143500  0.246750  0.178125  0.099875   
2022-01-04  0.096250  0.137250  0.130875  0.237500  0.126375  0.120750   
2022-01-05  0.150750  0.099250  0.060125  0.106750  0.143875  0.260750   
2022-01-06  0.180750  0.142125  0.119000  0.078625  0.143875  0.069125   
2022-01-07  0.342500  0.142125  0.279375  0.262750  0.193875  0.073250   
2022-01-10  0.150750  0.148375  0.100750  0.217125  0.210000  0.249125   
2022-01-11  0.090750  0.208375  0.286875  0.085750  0.206625  0.264875   
2022-01-12  0.148125  0.316250  0.116875  0.083625  0.126875  0.135625   
2022-01-13  0.089000  0.329875  0.297375  0.213250  0.213250  0.225625   
2022-01-14  0.149000  0.157750  0.304250  0.204500  0.193750  0.215500   
2022-01-18  0.087750  0.202125  0.134250  0.131375  0.143250  0.275625   
2022-01-19  0.190375  0.080250  0.051375  0.081375  0.213250  0.227250   
2022-01-20  0.143250  0.210250  0.152250  0.083250  0.213250  0.072875   
2022-01-21  0.149625  0.064375  0.152250  0.231750  0.123500  0.078375   
2022-01-24  0.332750  0.075250  0.049625  0.117250  0.216875  0.134750   
2022-01-25  0.106375  0.075250  0.132500  0.127750  0.136875  0.229500   
2022-01-26  0.192500  0.190125  0.291500  0.083125  0.136875  0.073875   
2022-01-27  0.092500  0.065250  0.096250  0.257125  0.135125  0.273875   
2022-01-28  0.183250  0.177625  0.052375  0.129250  0.167625  0.229125   
2022-01-31  0.093250  0.187625  0.296250  0.134250  0.206875  0.079125   
2022-02-01  0.097625  0.204375  0.060375  0.077375  0.206875  0.278500   
2022-02-02  0.102750  0.199500  0.300375  0.079125  0.146625  0.290250   
2022-02-03  0.177250  0.184125  0.059625  0.199125  0.223500  0.076875   
2022-02-04  0.182375  0.326750  0.059375  0.160500  0.153500  0.218625   
2022-02-07  0.092375  0.062375  0.115750  0.208750  0.220125  0.082500   
2022-02-08  0.156750  0.069625  0.274875  0.088750  0.120375  0.072500   
2022-02-09  0.166125  0.157375  0.059625  0.083750  0.251625  0.079875   
2022-02-10  0.106125  0.145625  0.063250  0.145875  0.193750  0.067125   
2022-02-11  0.152750  0.295625  0.124250  0.085875  0.213250  0.204375   
2022-02-14  0.106125  0.275750  0.068625  0.082500  0.115750  0.077250   
2022-02-15  0.096125  0.261250  0.141250  0.092500  0.205750  0.094500   
2022-02-16  0.106125  0.108875  0.204625  0.092500  0.149125  0.187500   
2022-02-17  0.166750  0.089625  0.074625  0.085875  0.145750  0.194500   
2022-02-18  0.091875  0.210625  0.071750  0.211250  0.203500  0.094500   
2022-02-22  0.095250  0.152875  0.194250  0.207875  0.244500  0.199125   
2022-02-23  0.103750

In [ ]:
RPS_2m.mean(axis=1).mean()

0.1616166666666667

In [ ]:
RPS_2m.mean(axis=1)

date
2021-12-08    0.153539
2021-12-09    0.168289
2021-12-10    0.153294
2021-12-13    0.161628
2021-12-14    0.150572
2021-12-15    0.151539
2021-12-16    0.151011
2021-12-17    0.166478
2021-12-20    0.150806
2021-12-21    0.166722
2021-12-22    0.169022
2021-12-23    0.162139
2021-12-27    0.157444
2021-12-28    0.163144
2021-12-29    0.163106
2021-12-30    0.181428
2021-12-31    0.150822
2022-01-03    0.155383
2022-01-04    0.178078
2022-01-05    0.171228
2022-01-06    0.169656
2022-01-07    0.169122
2022-01-10    0.165000
2022-01-11    0.146894
2022-01-12    0.172044
2022-01-13    0.176672
2022-01-14    0.155594
2022-01-18    0.139400
2022-01-19    0.158917
2022-01-20    0.160644
2022-01-21    0.145261
2022-01-24    0.181722
2022-01-25    0.148689
2022-01-26    0.168306
2022-01-27    0.161128
2022-01-28    0.164839
2022-01-31    0.149522
2022-02-01    0.152256
2022-02-02    0.153867
2022-02-03    0.170050
2022-02-04    0.173189
2022-02-07    0.150322
2022-02-08    0.151994
2022-0

#####3 months (60 working days)
***

In [ ]:
t_3m=pred(q1_1,139)
t_3m=pd.DataFrame.from_dict(t_3m)
t_3m.set_index('date')
RPS_3m= RPS_data(t_3m,rd)
RPS_3m= create_RPS(t_3m,RPS_3m)
RPS_3m
print(RPS_3m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-01-26    4
Name: UNH, dtype: int64 mikos 60
4 defaultdict(<class 'int'>, {2: 11, 4: 18, 3: 14, 5: 12, 1: 5})
imera : 2022-01-28
arxi insample Date
2021-11-02    4
Name: UNH, dtype: int64 kai telos insample Date
2022-01-26    4
2022-01-27    2
Name: UNH, dtype: int64 mikos 60
2 defaultdict(<class 'int'>, {4: 18, 3: 14, 2: 11, 5: 12, 1: 5})
imera : 2022-01-31
arxi insample Date
2021-11-03    3
Name: UNH, dtype: int64 kai telos insample Date
2022-01-27    2
2022-01-28    3
Name: UNH, dtype: int64 mikos 60
3 defaultdict(<class 'int'>, {3: 15, 2: 11, 5: 12, 4: 17, 1: 5})
imera : 2022-02-01
arxi insample Date
2021-11-04    2
Name: UNH, dtype: int64 kai telos insample Date
2022-01-28    3
2022-01-31    1
Name: UNH, dtype: int64 mikos 60
1 defaultdict(<class 'int'>, {2: 11, 5: 12, 4: 17, 1: 6, 3: 14})
imera : 2022-02-02
arxi insample Date
2021-11-05    5
Name: UNH, dtype: int64 kai telos insample Date
2022-01-31    1
2022-02-01    5
N

In [ ]:
RPS_3m

ABBV       AEP       AIZ      ALLE      AMAT       AMP  \
date                                                                     
2021-12-08  0.213556  0.078833  0.228778  0.113389  0.176556  0.077889   
2021-12-09  0.141722  0.221167  0.046833  0.126111  0.124167  0.215722   
2021-12-10  0.070000  0.132667  0.094444  0.106111  0.181000  0.095722   
2021-12-13  0.296667  0.251167  0.094444  0.109833  0.161000  0.101833   
2021-12-14  0.194556  0.124500  0.045278  0.103500  0.173167  0.098722   
2021-12-15  0.194556  0.119000  0.048833  0.125722  0.269889  0.306833   
2021-12-16  0.154722  0.111389  0.048833  0.081667  0.255000  0.302500   
2021-12-17  0.154722  0.108056  0.094444  0.210167  0.257500  0.065056   
2021-12-20  0.092944  0.216556  0.048278  0.283500  0.170833  0.284056   
2021-12-21  0.152667  0.277500  0.154944  0.283500  0.166778  0.064056   
2021-12-22  0.186000  0.109000  0.157667  0.103500  0.269000  0.065667   
2021-12-23  0.190833  0.115222  0.339000  0.086111  0.151000  0.093000   
2021-12-27  0.199500  0.121889  0.215278  0.085889  0.284333  0.213278   
2021-12-28  0.075000  0.123167  0.056778  0.231889  0.132722  0.299667   
2021-12-29  0.295000  0.119389  0.082111  0.086389  0.141722  0.093000   
2021-12-30  0.146333  0.259500  0.081722  0.245000  0.132722  0.098556   
2021-12-31  0.079667  0.115833  0.057167  0.133167  0.117667  0.100833   
2022-01-03  0.196722  0.245833  0.145667  0.239722  0.190778  0.130333   
2022-01-04  0.109500  0.130333  0.140944  0.242778  0.137444  0.097000   
2022-01-05  0.194167  0.105278  0.063000  0.101389  0.121889  0.226611   
2022-01-06  0.140111  0.131500  0.143889  0.089444  0.119167  0.072222   
2022-01-07  0.304500  0.131500  0.303500  0.249111  0.157056  0.073000   
2022-01-10  0.182722  0.135167  0.085444  0.229000  0.260111  0.229944   
2022-01-11  0.105000  0.235167  0.309167  0.088056  0.267667  0.289944   
2022-01-12  0.182111  0.289056  0.145444  0.088167  0.134333  0.144167   
2022-01-13  0.082722  0.290333  0.315167  0.226778  0.166778  0.229889   
2022-01-14  0.174500  0.143667  0.315167  0.220444  0.155222  0.229889   
2022-01-18  0.103333  0.223667  0.148500  0.118833  0.183722  0.290722   
2022-01-19  0.156667  0.099611  0.065444  0.081944  0.255389  0.237444   
2022-01-20  0.169389  0.213000  0.144389  0.081944  0.250778  0.070778   
2022-01-21  0.173889  0.063889  0.140500  0.235889  0.135389  0.074111   
2022-01-24  0.316167  0.095667  0.060500  0.110167  0.168722  0.131167   
2022-01-25  0.091667  0.091833  0.140000  0.110167  0.167500  0.254167   
2022-01-26  0.151667  0.208111  0.298889  0.080667  0.170111  0.070333   
2022-01-27  0.101500  0.084500  0.093056  0.257944  0.162556  0.264500   
2022-01-28  0.156056  0.153111  0.059722  0.126111  0.143556  0.251889   
2022-01-31  0.109222  0.206444  0.313333  0.122000  0.226056  0.071889   
2022-02-01  0.089222  0.206444  0.060000  0.076000  0.220500  0.259000   
2022-02-02  0.106944  0.206444  0.309667  0.076000  0.151444  0.266333   
2022-02-03  0.162833  0.161556  0.055667  0.211278  0.207722  0.072333   
2022-02-04  0.170611  0.310167  0.054500  0.138889  0.149167  0.238500   
2022-02-07  0.097278  0.082111  0.118667  0.214611  0.220333  0.075833   
2022-02-08  0.159333  0.081389  0.292000  0.101278  0.118167  0.092778   
2022-02-09  0.159944  0.154111  0.052389  0.081278  0.218167  0.072778   
2022-02-10  0.096889  0.145056  0.052389  0.134611  0.211500  0.088056   
2022-02-11  0.185000  0.320778  0.113000  0.077944  0.224944  0.228333   
2022-02-14  0.091667  0.305667  0.053000  0.075667  0.113167  0.093833   
2022-02-15  0.098333  0.295222  0.116111  0.095667  0.219833  0.075000   
2022-02-16  0.091000  0.093278  0.256944  0.093556  0.146611  0.150500   
2022-02-17  0.194611  0.074444  0.109444  0.079444  0.131333  0.217444   
2022-02-18  0.103778  0.215222  0.109444  0.215000  0.219833  0.081889   
2022-02-22  0.109889  0.150833  0.255722  0.215000  0.222000  0.206389   
2022-02-23  0.112500

In [ ]:
RPS_3m.mean(axis=1)


date
2021-12-08    0.156788
2021-12-09    0.163978
2021-12-10    0.152494
2021-12-13    0.160143
2021-12-14    0.152684
2021-12-15    0.152798
2021-12-16    0.158541
2021-12-17    0.163993
2021-12-20    0.150338
2021-12-21    0.163328
2021-12-22    0.163069
2021-12-23    0.160551
2021-12-27    0.160165
2021-12-28    0.163412
2021-12-29    0.157022
2021-12-30    0.179069
2021-12-31    0.149286
2022-01-03    0.159198
2022-01-04    0.176864
2022-01-05    0.168731
2022-01-06    0.163874
2022-01-07    0.164852
2022-01-10    0.162625
2022-01-11    0.152798
2022-01-12    0.167686
2022-01-13    0.172464
2022-01-14    0.156133
2022-01-18    0.144630
2022-01-19    0.156763
2022-01-20    0.162027
2022-01-21    0.150089
2022-01-24    0.171914
2022-01-25    0.151037
2022-01-26    0.167131
2022-01-27    0.152578
2022-01-28    0.169047
2022-01-31    0.148415
2022-02-01    0.145484
2022-02-02    0.148973
2022-02-03    0.170193
2022-02-04    0.170096
2022-02-07    0.153123
2022-02-08    0.156570
2022-0

In [ ]:
RPS_3m.mean(axis=1).mean()

0.1603325514403292

#####6 months
***

In [ ]:
t_6m=pred(q1_1,79)
t_6m=pd.DataFrame.from_dict(t_6m)
t_6m.set_index('date')
RPS_6m= RPS_data(t_6m,rd)
RPS_6m= create_RPS(t_6m,RPS_6m)
RPS_6m
print(RPS_6m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-01-26    4
Name: UNH, dtype: int64 mikos 120
4 defaultdict(<class 'int'>, {1: 16, 3: 30, 2: 22, 5: 27, 4: 25})
imera : 2022-01-28
arxi insample Date
2021-08-09    3
Name: UNH, dtype: int64 kai telos insample Date
2022-01-26    4
2022-01-27    2
Name: UNH, dtype: int64 mikos 120
2 defaultdict(<class 'int'>, {3: 30, 1: 15, 2: 23, 5: 27, 4: 25})
imera : 2022-01-31
arxi insample Date
2021-08-10    1
Name: UNH, dtype: int64 kai telos insample Date
2022-01-27    2
2022-01-28    3
Name: UNH, dtype: int64 mikos 120
3 defaultdict(<class 'int'>, {1: 15, 2: 23, 5: 27, 3: 30, 4: 25})
imera : 2022-02-01
arxi insample Date
2021-08-11    2
Name: UNH, dtype: int64 kai telos insample Date
2022-01-28    3
2022-01-31    1
Name: UNH, dtype: int64 mikos 120
1 defaultdict(<class 'int'>, {2: 23, 5: 27, 3: 30, 1: 15, 4: 25})
imera : 2022-02-02
arxi insample Date
2021-08-12    5
Name: UNH, dtype: int64 kai telos insample Date
2022-01-31    1
2022-02-0

In [ ]:
RPS_6m

ABBV       AEP       AIZ      ALLE      AMAT       AMP  \
date                                                                     
2021-12-08  0.233181  0.074361  0.252111  0.118972  0.164778  0.078125   
2021-12-09  0.134028  0.233014  0.058778  0.118972  0.119014  0.215972   
2021-12-10  0.071625  0.124250  0.092458  0.114292  0.180306  0.094431   
2021-12-13  0.281986  0.250861  0.091417  0.114292  0.159750  0.097458   
2021-12-14  0.214125  0.117528  0.056708  0.114292  0.188625  0.099306   
2021-12-15  0.208097  0.117528  0.057125  0.119583  0.252486  0.283292   
2021-12-16  0.149639  0.115514  0.055750  0.079583  0.245292  0.285417   
2021-12-17  0.151931  0.113597  0.092417  0.228333  0.246417  0.073958   
2021-12-20  0.089306  0.243597  0.057125  0.257139  0.159750  0.277472   
2021-12-21  0.148583  0.242181  0.133431  0.255736  0.180306  0.076250   
2021-12-22  0.205958  0.115514  0.133056  0.115736  0.253639  0.077208   
2021-12-23  0.208583  0.119500  0.300083  0.082375  0.175208  0.097514   
2021-12-27  0.210403  0.119500  0.249736  0.082375  0.265958  0.209028   
2021-12-28  0.073319  0.120097  0.056042  0.235569  0.123528  0.289028   
2021-12-29  0.289917  0.121458  0.092708  0.082917  0.168097  0.097986   
2021-12-30  0.147292  0.242778  0.093750  0.239583  0.124014  0.101472   
2021-12-31  0.072833  0.118125  0.057125  0.129639  0.123625  0.102708   
2022-01-03  0.214708  0.249569  0.123569  0.239583  0.171917  0.132528   
2022-01-04  0.098042  0.117736  0.123569  0.242319  0.125250  0.099903   
2022-01-05  0.212083  0.121639  0.058028  0.115000  0.121917  0.210208   
2022-01-06  0.139847  0.116264  0.121361  0.083750  0.121917  0.080167   
2022-01-07  0.288292  0.119514  0.276194  0.256542  0.175819  0.079458   
2022-01-10  0.207153  0.120958  0.103208  0.229139  0.247583  0.213903   
2022-01-11  0.100125  0.248250  0.275250  0.081764  0.249236  0.297931   
2022-01-12  0.209028  0.241583  0.121708  0.081250  0.128819  0.142833   
2022-01-13  0.072819  0.241583  0.283028  0.233903  0.176833  0.206167   
2022-01-14  0.206917  0.117653  0.288250  0.236583  0.170833  0.203306   
2022-01-18  0.100250  0.248917  0.127153  0.113250  0.166833  0.295861   
2022-01-19  0.143583  0.115611  0.056083  0.078569  0.247819  0.215194   
2022-01-20  0.206458  0.241736  0.130764  0.079194  0.240625  0.078528   
2022-01-21  0.203514  0.072333  0.129417  0.239736  0.129167  0.078597   
2022-01-24  0.293514  0.114194  0.055833  0.113611  0.182944  0.137417   
2022-01-25  0.075792  0.114194  0.122306  0.112958  0.159167  0.216264   
2022-01-26  0.153750  0.240861  0.285639  0.078250  0.162944  0.075639   
2022-01-27  0.091361  0.110972  0.099542  0.248250  0.162028  0.285639   
2022-01-28  0.158028  0.124194  0.055139  0.115569  0.132028  0.222403   
2022-01-31  0.094597  0.240861  0.298458  0.115569  0.245861  0.075736   
2022-02-01  0.077500  0.242778  0.055458  0.080931  0.250167  0.279069   
2022-02-02  0.095139  0.239528  0.307542  0.082306  0.169569  0.279069   
2022-02-03  0.151806  0.126194  0.053472  0.226403  0.175875  0.075736   
2022-02-04  0.150986  0.244125  0.053472  0.123069  0.127528  0.219431   
2022-02-07  0.094319  0.114125  0.135819  0.227750  0.256931  0.077139   
2022-02-08  0.197250  0.115417  0.302153  0.112528  0.128639  0.088917   
2022-02-09  0.200542  0.118125  0.052139  0.083069  0.258639  0.074083   
2022-02-10  0.098028  0.114819  0.052417  0.123069  0.171972  0.086306   
2022-02-11  0.149514  0.241403  0.096042  0.083069  0.177972  0.209569   
2022-02-14  0.095208  0.241403  0.053722  0.081208  0.126625  0.091806   
2022-02-15  0.078542  0.238722  0.097375  0.110042  0.174528  0.075139   
2022-02-16  0.096083  0.122083  0.284139  0.108931  0.169125  0.146236   
2022-02-17  0.156181  0.078694  0.127472  0.085597  0.127528  0.215597   
2022-02-18  0.079014  0.240042  0.126208  0.213792  0.248486  0.076236   
2022-02-22  0.079917  0.122069  0.285861  0.212042  0.178486  0.211361   
2022-02-23  0.080972

In [ ]:
RPS_6m.mean(axis=1).mean()

0.15885165637860085

In [ ]:
RPS_6m.mean(axis=1)

date
2021-12-08    0.158595
2021-12-09    0.163057
2021-12-10    0.151713
2021-12-13    0.159515
2021-12-14    0.157008
2021-12-15    0.155915
2021-12-16    0.159578
2021-12-17    0.161957
2021-12-20    0.155010
2021-12-21    0.159313
2021-12-22    0.161751
2021-12-23    0.159327
2021-12-27    0.160646
2021-12-28    0.157579
2021-12-29    0.156792
2021-12-30    0.164656
2021-12-31    0.151867
2022-01-03    0.160941
2022-01-04    0.164355
2022-01-05    0.161321
2022-01-06    0.159185
2022-01-07    0.160127
2022-01-10    0.161706
2022-01-11    0.156440
2022-01-12    0.164986
2022-01-13    0.161770
2022-01-14    0.155342
2022-01-18    0.154073
2022-01-19    0.157566
2022-01-20    0.160115
2022-01-21    0.153656
2022-01-24    0.164551
2022-01-25    0.156031
2022-01-26    0.165171
2022-01-27    0.155922
2022-01-28    0.159760
2022-01-31    0.154266
2022-02-01    0.151678
2022-02-02    0.153994
2022-02-03    0.161681
2022-02-04    0.161276
2022-02-07    0.157554
2022-02-08    0.159973
2022-0

#####All the samples
***

In [ ]:
#Αυτή η συνάρτηση παίρνει τα data και κάνει τη dummy μέτρηση για το διάστημα ενός χρόνου (όσο οριστεί στην ουσία το insample) για μια μετοχή
n=dict() 
def dummy2(st,i):
  flag=False
  insample=st.iloc[:-i]
  print('arxi',insample.head(1),'kai telos ',insample.tail(1),'mikos',len(insample))
  # if(len(insample)!=253):
  #   print('---------------------------------------------------------------',flag)
  count=defaultdict(int)
  for word in insample.values:
    count[word]+=1
  print(word,count)
  count=sorted(count.items()) #list Η πρώτη τιμή είναι η κλάση και η δεύτερη πόσες φορές είδα τον αριθμό.
  temp=[]
  for k in range(5):
    flag=True
    for l in count:
      if(l[0]==k+1):
        temp.append(l[1]/len(insample))
        flag=False
        break
    if(flag):
      temp.append(0)
  # print(temp,count)
  data={
      'prediction':temp
  }
  forecast=pd.DataFrame(data)
  return forecast
# #για όλες τις μετοχές υπολογίζεται το counter τους
dummy2(rd3['ABBV'],60)


arxi Date
2021-03-01    3
Name: ABBV, dtype: int64 kai telos  Date
2022-04-01    2
Name: ABBV, dtype: int64 mikos 277
2 defaultdict(<class 'int'>, {3: 61, 2: 55, 1: 39, 4: 62, 5: 60})


prediction
0    0.140794
1    0.198556
2    0.220217
3    0.223827
4    0.216606

In [ ]:
def pred2(st):
  pred=dict()
  for j in st:
    temp=[]
    date=[]
    for i in range(59,1,-1):
      # print(i)
      date.append(q1_1[j].iloc[-i:-i+1].index.date[0])
      print(date)
      temp.append(dummy2(q1_1[j],i)['prediction'].values)
      # pred[q1_1[j].name]=temp
    #for the last day 
    date.append(q1_1[j].iloc[-1:].index.date[0])
    temp.append(dummy2(q1_1[j],1)['prediction'].values)
    pred[q1_1[j].name]=temp
  # print(date)
  pred['date']=date
  pred_final=pd.DataFrame.from_dict(pred)
  # pred_final['Date']=date
  # pred_final.set_index('Date')
  # print(pred_final)
  return pred_final


In [ ]:
t_all=pred2(q1_1)
t_all=pd.DataFrame.from_dict(t_all)
t_all.set_index('date')
RPS_all= RPS_data(t_all,rd)
RPS_all= create_RPS(t_all,RPS_all)
RPS_all
print(RPS_all.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
[datetime.date(2021, 12, 9), datetime.date(2021, 12, 10), datetime.date(2021, 12, 13), datetime.date(2021, 12, 14), datetime.date(2021, 12, 15), datetime.date(2021, 12, 16), datetime.date(2021, 12, 17), datetime.date(2021, 12, 20), datetime.date(2021, 12, 21), datetime.date(2021, 12, 22), datetime.date(2021, 12, 23), datetime.date(2021, 12, 27), datetime.date(2021, 12, 28), datetime.date(2021, 12, 29), datetime.date(2021, 12, 30), datetime.date(2021, 12, 31), datetime.date(2022, 1, 3), datetime.date(2022, 1, 4), datetime.date(2022, 1, 5), datetime.date(2022, 1, 6), datetime.date(2022, 1, 7), datetime.date(2022, 1, 10), datetime.date(2022, 1, 11), datetime.date(2022, 1, 12), datetime.date(2022, 1, 13), datetime.date(2022, 1, 14), datetime.date(2022, 1, 18), datetime.date(2022, 1, 19), datetime.date(2022, 1, 20), datetime.date(2022, 1, 21), datetime.date(2022, 1, 24), datetime.date(2022, 1, 25), datetime.date(2022, 1, 26), datetime.d

In [ ]:
RPS_all

ABBV       AEP       AIZ      ALLE      AMAT       AMP  \
date                                                                     
2021-12-09  0.131267  0.231374  0.064111  0.113366  0.137792  0.239368   
2021-12-10  0.073175  0.121058  0.111704  0.119436  0.209747  0.108169   
2021-12-13  0.267290  0.261850  0.111825  0.119450  0.141605  0.109030   
2021-12-14  0.225034  0.118660  0.063192  0.118264  0.210856  0.109141   
2021-12-15  0.222811  0.117778  0.063557  0.114327  0.220655  0.270777   
2021-12-16  0.136485  0.116620  0.062933  0.076750  0.218486  0.271077   
2021-12-17  0.136433  0.116657  0.110121  0.249654  0.220309  0.067455   
2021-12-20  0.100540  0.255324  0.063196  0.243322  0.144419  0.268735   
2021-12-21  0.136596  0.237393  0.111858  0.243708  0.205821  0.068206   
2021-12-22  0.219893  0.117818  0.112721  0.116362  0.223562  0.068660   
2021-12-23  0.219314  0.119004  0.271274  0.076784  0.204193  0.107235   
2021-12-27  0.219821  0.119810  0.258936  0.076825  0.227124  0.235398   
2021-12-28  0.074308  0.113243  0.063828  0.250544  0.122109  0.271075   
2021-12-29  0.273480  0.113290  0.108488  0.077604  0.202084  0.108075   
2021-12-30  0.139080  0.236726  0.109336  0.251201  0.122708  0.109127   
2021-12-31  0.074866  0.117887  0.064370  0.120263  0.136468  0.109930   
2022-01-03  0.219962  0.258106  0.109350  0.250301  0.147026  0.120120   
2022-01-04  0.101092  0.114233  0.108335  0.238378  0.122972  0.108218   
2022-01-05  0.219050  0.117142  0.064742  0.113572  0.138040  0.236848   
2022-01-06  0.136304  0.114230  0.108165  0.078719  0.137378  0.070288   
2022-01-07  0.273870  0.115285  0.263336  0.242038  0.206372  0.070398   
2022-01-10  0.218648  0.115331  0.112062  0.246792  0.220291  0.235967   
2022-01-11  0.101579  0.256446  0.264893  0.078781  0.221388  0.273826   
2022-01-12  0.220241  0.239369  0.109343  0.078803  0.123527  0.125509   
2022-01-13  0.073874  0.240748  0.266910  0.246396  0.206099  0.232587   
2022-01-14  0.219638  0.117175  0.267216  0.245676  0.204255  0.231981   
2022-01-18  0.101610  0.251853  0.110379  0.116378  0.145205  0.274358   
2022-01-19  0.136107  0.113339  0.063384  0.078179  0.220022  0.234592   
2022-01-20  0.219861  0.250392  0.111289  0.078514  0.218079  0.070409   
2022-01-21  0.219321  0.075503  0.111401  0.246250  0.123977  0.070667   
2022-01-24  0.273030  0.112692  0.063058  0.116032  0.208480  0.124434   
2022-01-25  0.075246  0.111710  0.109464  0.116767  0.142862  0.237124   
2022-01-26  0.136582  0.248132  0.265221  0.078526  0.143940  0.069550   
2022-01-27  0.101291  0.109784  0.111407  0.244081  0.143239  0.272559   
2022-01-28  0.137597  0.120857  0.063239  0.117828  0.141223  0.235731   
2022-01-31  0.102345  0.249435  0.267642  0.117847  0.218689  0.070324   
2022-02-01  0.075685  0.250741  0.063463  0.077836  0.218935  0.272146   
2022-02-02  0.103127  0.250050  0.268882  0.077874  0.144217  0.273105   
2022-02-03  0.136516  0.120817  0.063035  0.240926  0.209099  0.070562   
2022-02-04  0.137197  0.245538  0.063149  0.119874  0.139347  0.234389   
2022-02-07  0.101264  0.110427  0.109678  0.243238  0.220532  0.071079   
2022-02-08  0.214909  0.111136  0.266921  0.113860  0.121125  0.101448   
2022-02-09  0.216198  0.118510  0.063035  0.078194  0.223090  0.069899   
2022-02-10  0.102374  0.117529  0.063136  0.119182  0.207965  0.101011   
2022-02-11  0.137894  0.245762  0.113022  0.077870  0.209501  0.232515   
2022-02-14  0.101058  0.243743  0.063554  0.077231  0.120896  0.102637   
2022-02-15  0.076559  0.241750  0.114680  0.113625  0.208069  0.070935   
2022-02-16  0.100688  0.114572  0.258459  0.112996  0.145150  0.129296   
2022-02-17  0.140522  0.078125  0.104947  0.077900  0.137468  0.230908   
2022-02-18  0.077038  0.249819  0.105073  0.240833  0.220227  0.071957   
2022-02-22  0.077491  0.118776  0.257453  0.241165  0.210390  0.229442   
2022-02-23  0.077947  0.118788  0.064034  0.239232  0.218696  0.102131   
2022-02-24  0.078112

In [ ]:
RPS_all.mean(axis=1)

date
2021-12-09    0.162132
2021-12-10    0.153035
2021-12-13    0.159530
2021-12-14    0.156886
2021-12-15    0.158318
2021-12-16    0.161261
2021-12-17    0.162634
2021-12-20    0.158279
2021-12-21    0.159581
2021-12-22    0.161062
2021-12-23    0.158504
2021-12-27    0.159351
2021-12-28    0.156221
2021-12-29    0.155595
2021-12-30    0.161558
2021-12-31    0.156051
2022-01-03    0.161503
2022-01-04    0.162518
2022-01-05    0.160894
2022-01-06    0.158928
2022-01-07    0.156364
2022-01-10    0.162513
2022-01-11    0.157275
2022-01-12    0.161823
2022-01-13    0.160824
2022-01-14    0.157374
2022-01-18    0.156289
2022-01-19    0.157171
2022-01-20    0.159065
2022-01-21    0.157477
2022-01-24    0.158657
2022-01-25    0.156417
2022-01-26    0.161546
2022-01-27    0.159081
2022-01-28    0.158403
2022-01-31    0.154988
2022-02-01    0.156526
2022-02-02    0.157053
2022-02-03    0.157594
2022-02-04    0.159959
2022-02-07    0.157166
2022-02-08    0.158521
2022-02-09    0.156870
2022-0

In [ ]:
RPS_all.mean(axis=1).mean()

0.15866156206662332

####**For 3 April-29 April**

#####Prepare the dataset with the dummy data 

In [ ]:
#cut the dataset(with the ranks) we have until 3 April 
q1_1=rd3.copy()
q1_1=q1_1.loc[(q1_1.index<='2022-04-03') & (q1_1.index>'2021-04-01')]
q1_1

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-04-05     2    4    4     5     1    2     3    4    5    3  ...    4   
2021-04-06     2    2    5     2     2    4     5    4    1    4  ...    5   
2021-04-07     5    2    3     2     3    2     4    1    5    3  ...    1   
2021-04-08     4    1    4     3     1    5     5    2    5    2  ...    5   
2021-04-09     4    3    4     2     1    5     3    4    2    2  ...    5   
...          ...  ...  ...   ...   ...  ...   ...  ...  ...  ...  ...  ...   
2022-03-28     1    3    1     3     4    2     1    5    5    2  ...    2   
2022-03-29     5    5    4     2     1    3     1    1    2    3  ...    3   
2022-03-30     4    5    5     1     1    1     2    3    3    3  ...    3   
2022-03-31     3    5    5     4     1    1     2    5    3    2  ...    2   
2022-04-01     2    2    1     3     4    3     5    1    2    4  ...    1   

            PYPL  RE  ROL  ROST  UNH  URI  V  VRSK  XOM  
Date                                                     
2021-04-05     5   5    3     4    1    1  3     2    2  
2021-04-06     5   5    1     3    3    1  3     1    4  
2021-04-07     5   2    5     5    3    3  4     4    1  
2021-04-08     3   3    4     3    5    4  3     3    1  
2021-04-09     5   3    4     2    3    5  1     2    1  
...          ...  ..  ...   ...  ...  ... ..   ...  ...  
2022-03-28     5   3    4     5    1    2  5     3    1  
2022-03-29     1   5    5     1    5    2  1     5    5  
2022-03-30     1   4    4     2    2    3  4     4    3  
2022-03-31     3   5    1     2    3    2  5     2    3  
2022-04-01     5   1    4     5    2    1  4     4    3  

[253 rows x 45 columns]

In [ ]:
#April '21
#save the values of the month
# april_21 = rd3.loc[(rd3.index < '2021-04-30') & (rd3.index > '2021-04-04')]
# april_21

In [ ]:
#april 22
# april_22 = rd3.loc[(rd3.index > '2022-04-01') & (rd3.index <= '2022-04-30')]
# april_22

In [ ]:
# for i in april_22:
#   april_22[i] = april_21[i].values
# april_22

In [ ]:
#now that we have the new "dummy" month all we have to do is to join it with the original dataframe
# q1_1 = pd.concat([q1_1,april_22])
# q1_1

#####15 days
***

In [ ]:
t_15d=pred(q1_1,180)
t_15d=pd.DataFrame.from_dict(t_15d)
t_15d.set_index('date')
RPS_15d= RPS_data(t_15d,rd)
RPS_15d= create_RPS(t_15d,RPS_15d)
RPS_15d
print(RPS_15d.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-02-24    5
Name: UNH, dtype: int64 mikos 15
5 defaultdict(<class 'int'>, {2: 6, 3: 5, 4: 2, 5: 2})
imera : 2022-02-28
arxi insample Date
2022-02-04    3
Name: UNH, dtype: int64 kai telos insample Date
2022-02-24    5
2022-02-25    4
Name: UNH, dtype: int64 mikos 15
4 defaultdict(<class 'int'>, {3: 5, 4: 3, 2: 5, 5: 2})
imera : 2022-03-01
arxi insample Date
2022-02-07    4
Name: UNH, dtype: int64 kai telos insample Date
2022-02-25    4
2022-02-28    5
Name: UNH, dtype: int64 mikos 15
5 defaultdict(<class 'int'>, {4: 3, 3: 4, 2: 5, 5: 3})
imera : 2022-03-02
arxi insample Date
2022-02-08    3
Name: UNH, dtype: int64 kai telos insample Date
2022-02-28    5
2022-03-01    3
Name: UNH, dtype: int64 mikos 15
3 defaultdict(<class 'int'>, {3: 5, 2: 5, 4: 2, 5: 3})
imera : 2022-03-03
arxi insample Date
2022-02-09    2
Name: UNH, dtype: int64 kai telos insample Date
2022-03-01    3
2022-03-02    4
Name: UNH, dtype: int64 mikos 15
4 defaul

In [ ]:
RPS_15d

ABBV       AEP       AIZ      ALLE      AMAT       AMP  \
date                                                                     
2022-01-06  0.147556  0.122667  0.076444  0.109333  0.141333  0.095111   
2022-01-07  0.309333  0.128889  0.214222  0.271111  0.154667  0.110222   
2022-01-10  0.168889  0.128889  0.148444  0.211556  0.221333  0.190222   
2022-01-11  0.119111  0.275556  0.205333  0.098667  0.221333  0.360889   
2022-01-12  0.201778  0.269333  0.080000  0.112000  0.141333  0.208000   
2022-01-13  0.063111  0.304000  0.226667  0.245333  0.208000  0.190222   
2022-01-14  0.229333  0.186667  0.216889  0.222222  0.208000  0.190222   
2022-01-18  0.127111  0.155556  0.062222  0.155556  0.118222  0.292444   
2022-01-19  0.127111  0.056000  0.062222  0.101333  0.158222  0.212444   
2022-01-20  0.222222  0.164444  0.098667  0.112000  0.115556  0.097778   
2022-01-21  0.240889  0.090667  0.115556  0.185778  0.157333  0.097778   
2022-01-24  0.267556  0.057778  0.046222  0.172444  0.264889  0.211556   
2022-01-25  0.098667  0.048000  0.112889  0.168000  0.102222  0.209778   
2022-01-26  0.148444  0.133333  0.262222  0.093333  0.118222  0.073778   
2022-01-27  0.121778  0.033778  0.093333  0.318222  0.118222  0.316444   
2022-01-28  0.165333  0.247111  0.043556  0.171556  0.207111  0.235556   
2022-01-31  0.124444  0.190222  0.337778  0.158222  0.186667  0.075556   
2022-02-01  0.101333  0.202667  0.041778  0.069333  0.200000  0.275556   
2022-02-02  0.129778  0.182222  0.335111  0.076444  0.133333  0.272889   
2022-02-03  0.151111  0.226667  0.038222  0.162667  0.275556  0.080889   
2022-02-04  0.178667  0.331556  0.038222  0.173333  0.168889  0.267556   
2022-02-07  0.098667  0.051556  0.104889  0.209778  0.176000  0.083556   
2022-02-08  0.178667  0.071111  0.261333  0.108444  0.086222  0.082667   
2022-02-09  0.181333  0.120889  0.062222  0.082667  0.274667  0.058667   
2022-02-10  0.101333  0.094222  0.062222  0.149333  0.194667  0.063111   
2022-02-11  0.181333  0.240889  0.173333  0.068444  0.200889  0.183111   
2022-02-14  0.093333  0.240889  0.080000  0.057778  0.076444  0.069333   
2022-02-15  0.106667  0.195556  0.179556  0.105778  0.186667  0.104000   
2022-02-16  0.093333  0.189333  0.166222  0.100444  0.173333  0.205333   
2022-02-17  0.190222  0.127111  0.054222  0.093333  0.088889  0.181333   
2022-02-18  0.104889  0.280000  0.054222  0.178667  0.274667  0.112000   
2022-02-22  0.119111  0.109333  0.133333  0.178667  0.246222  0.150222   
2022-02-23  0.141333  0.118222  0.122667  0.178667  0.219556  0.096889   
2022-02-24  0.150222  0.104889  0.496000  0.136889  0.092444  0.293333   
2022-02-25  0.361778  0.098667  0.496000  0.064000  0.132444  0.186667   
2022-02-28  0.141333  0.186667  0.037333  0.144889  0.210667  0.081778   
2022-03-01  0.091556  0.186667  0.106667  0.240889  0.187556  0.261333   
2022-03-02  0.104889  0.186667  0.114667  0.104000  0.187556  0.280889   
2022-03-03  0.202667  0.186667  0.461333  0.061333  0.209778  0.094222   
2022-03-04  0.166222  0.072000  0.112000  0.168889  0.143111  0.090667   
2022-03-07  0.166222  0.112000  0.045333  0.288889  0.068444  0.224000   
2022-03-08  0.208000  0.402667  0.095111  0.101333  0.282667  0.240889   
2022-03-09  0.097778  0.229333  0.072000  0.300444  0.169778  0.147556   
2022-03-10  0.293333  0.148444  0.172444  0.247111  0.128889  0.158222   
2022-03-11  0.297778  0.112000  0.072000  0.055111  0.138667  0.152000   
2022-03-14  0.334222  0.392889  0.058667  0.268444  0.352000  0.257778   
2022-03-15  0.194667  0.069333  0.165333  0.160000  0.181333  0.145778   
2022-03-16  0.293333  0.121778  0.049778  0.176000  0.250667  0.068444   
2022-03-17  0.349333  0.136000  0.396444  0.084444  0.101333  0.087111   
2022-03-18  0.349333  0.115556  0.111111  0.280889  0.117333  0.056000   
2022-03-21  0.196444  0.136000  0.164444  0.115556  0.117333  0.275556   
2022-03-22  0.069333  0.271111  0.183111  0.333333  0.104000  0.336000   
2022-03-23  0.061333

In [ ]:
RPS_15d.mean(axis=1)

date
2022-01-06    0.164188
2022-01-07    0.169719
2022-01-10    0.153837
2022-01-11    0.158143
2022-01-12    0.185284
2022-01-13    0.167032
2022-01-14    0.163793
2022-01-18    0.128395
2022-01-19    0.167230
2022-01-20    0.157590
2022-01-21    0.140128
2022-01-24    0.214123
2022-01-25    0.146647
2022-01-26    0.165412
2022-01-27    0.165965
2022-01-28    0.183743
2022-01-31    0.157748
2022-02-01    0.154035
2022-02-02    0.150953
2022-02-03    0.174736
2022-02-04    0.180267
2022-02-07    0.151348
2022-02-08    0.158183
2022-02-09    0.166479
2022-02-10    0.162331
2022-02-11    0.163160
2022-02-14    0.158064
2022-02-15    0.164109
2022-02-16    0.179319
2022-02-17    0.153284
2022-02-18    0.172840
2022-02-22    0.163556
2022-02-23    0.155575
2022-02-24    0.198795
2022-02-25    0.196267
2022-02-28    0.146291
2022-03-01    0.154193
2022-03-02    0.165057
2022-03-03    0.200257
2022-03-04    0.142301
2022-03-07    0.125867
2022-03-08    0.151190
2022-03-09    0.155773
2022-0

In [ ]:
RPS_15d.mean(axis=1).mean()

0.1642804938271605

#####One Month (20 working days)

In [ ]:
t_1m=pred(q1_1,175)
t_1m=pd.DataFrame.from_dict(t_1m)
t_1m.set_index('date')
RPS_1m= RPS_data(t_1m,rd)
RPS_1m= create_RPS(t_1m,RPS_1m)
RPS_1m
print(RPS_1m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-02-24    5
Name: UNH, dtype: int64 mikos 20
5 defaultdict(<class 'int'>, {2: 7, 3: 6, 1: 1, 5: 4, 4: 2})
imera : 2022-02-28
arxi insample Date
2022-01-28    3
Name: UNH, dtype: int64 kai telos insample Date
2022-02-24    5
2022-02-25    4
Name: UNH, dtype: int64 mikos 20
4 defaultdict(<class 'int'>, {3: 6, 1: 1, 5: 4, 2: 6, 4: 3})
imera : 2022-03-01
arxi insample Date
2022-01-31    1
Name: UNH, dtype: int64 kai telos insample Date
2022-02-25    4
2022-02-28    5
Name: UNH, dtype: int64 mikos 20
5 defaultdict(<class 'int'>, {1: 1, 5: 5, 2: 6, 3: 5, 4: 3})
imera : 2022-03-02
arxi insample Date
2022-02-01    5
Name: UNH, dtype: int64 kai telos insample Date
2022-02-28    5
2022-03-01    3
Name: UNH, dtype: int64 mikos 20
3 defaultdict(<class 'int'>, {5: 5, 2: 6, 3: 6, 4: 3})
imera : 2022-03-03
arxi insample Date
2022-02-02    5
Name: UNH, dtype: int64 kai telos insample Date
2022-03-01    3
2022-03-02    4
Name: UNH, dtype: int64

In [ ]:
RPS_1m

ABBV     AEP     AIZ    ALLE    AMAT     AMP    AMZN     AVB  \
date                                                                         
2022-01-06  0.2170  0.1630  0.0950  0.0775  0.1470  0.0775  0.3470  0.3245   
2022-01-07  0.3780  0.1770  0.2565  0.2775  0.1870  0.0805  0.1575  0.2245   
2022-01-10  0.1380  0.1675  0.1165  0.2070  0.2270  0.2005  0.0710  0.3150   
2022-01-11  0.0930  0.2070  0.2565  0.0945  0.2625  0.3300  0.1905  0.0895   
2022-01-12  0.1770  0.2870  0.1050  0.0945  0.1510  0.2015  0.2990  0.1710   
2022-01-13  0.0710  0.2870  0.2635  0.2050  0.1805  0.1770  0.0870  0.1710   
2022-01-14  0.1965  0.1470  0.2635  0.1890  0.1455  0.1695  0.3155  0.1860   
2022-01-18  0.1115  0.1955  0.0950  0.1415  0.1605  0.3185  0.0780  0.0460   
2022-01-19  0.1240  0.0910  0.0675  0.0885  0.2070  0.1785  0.1350  0.0495   
2022-01-20  0.2025  0.1925  0.1065  0.1015  0.1690  0.1025  0.1140  0.2495   
2022-01-21  0.2170  0.0830  0.0990  0.2430  0.1605  0.0995  0.0950  0.0695   
2022-01-24  0.2780  0.0630  0.0610  0.1275  0.2605  0.1490  0.3785  0.0495   
2022-01-25  0.0910  0.0510  0.0650  0.1495  0.1075  0.2595  0.1185  0.0710   
2022-01-26  0.1375  0.1665  0.2075  0.0975  0.1205  0.0780  0.2340  0.3510   
2022-01-27  0.1250  0.0390  0.1450  0.3075  0.1075  0.3055  0.0995  0.0455   
2022-01-28  0.1290  0.2100  0.0565  0.1710  0.2065  0.2055  0.0875  0.0855   
2022-01-31  0.1305  0.1745  0.2730  0.1830  0.1690  0.0925  0.1805  0.2835   
2022-02-01  0.0990  0.1825  0.0540  0.0830  0.1550  0.3325  0.0970  0.1100   
2022-02-02  0.1305  0.1750  0.3085  0.0900  0.1245  0.3300  0.1915  0.1115   
2022-02-03  0.1305  0.1950  0.0485  0.1545  0.2380  0.0830  0.1075  0.1190   
2022-02-04  0.1515  0.3350  0.0465  0.1855  0.1650  0.2230  0.1080  0.0665   
2022-02-07  0.1085  0.0515  0.1395  0.2005  0.2175  0.0855  0.2680  0.0680   
2022-02-08  0.1790  0.0580  0.2970  0.0910  0.0975  0.0655  0.1115  0.0790   
2022-02-09  0.1815  0.1755  0.0450  0.0745  0.2430  0.0725  0.1745  0.1215   
2022-02-10  0.1185  0.1505  0.0450  0.1590  0.2430  0.0750  0.2650  0.2250   
2022-02-11  0.1790  0.3105  0.1495  0.0705  0.2495  0.2355  0.1450  0.1050   
2022-02-14  0.0990  0.2700  0.0580  0.0630  0.0975  0.1135  0.2495  0.0945   
2022-02-15  0.1010  0.2325  0.1710  0.1105  0.2345  0.0745  0.2495  0.1975   
2022-02-16  0.0925  0.1335  0.1660  0.1055  0.1555  0.1795  0.1285  0.0975   
2022-02-17  0.2185  0.1170  0.0530  0.0760  0.1110  0.1885  0.2030  0.1975   
2022-02-18  0.1125  0.2735  0.0530  0.1870  0.2555  0.0955  0.1030  0.1710   
2022-02-22  0.1270  0.1125  0.1530  0.1800  0.2345  0.1555  0.2085  0.0870   
2022-02-23  0.1270  0.1030  0.0930  0.1665  0.2415  0.0755  0.1085  0.2835   
2022-02-24  0.1150  0.1030  0.3770  0.1710  0.0815  0.3105  0.2035  0.1435   
2022-02-25  0.3170  0.1030  0.4245  0.0765  0.1170  0.1705  0.1910  0.2615   
2022-02-28  0.1635  0.2075  0.0415  0.1225  0.2445  0.0825  0.1845  0.2070   
2022-03-01  0.0850  0.1895  0.1415  0.2115  0.2210  0.3010  0.1115  0.0775   
2022-03-02  0.1050  0.1870  0.1390  0.1070  0.2285  0.3075  0.0955  0.2565   
2022-03-03  0.1965  0.1525  0.4780  0.0700  0.1550  0.0790  0.3030  0.2365   
2022-03-04  0.1585  0.0925  0.1045  0.1810  0.1805  0.0825  0.1650  0.0765   
2022-03-07  0.1585  0.1430  0.0510  0.2900  0.0910  0.2460  0.1330  0.2375   
2022-03-08  0.1890  0.3190  0.1110  0.1115  0.2755  0.2330  0.0930  0.2740   
2022-03-09  0.0890  0.1615  0.0985  0.2590  0.1755  0.1460  0.1250  0.0650   
2022-03-10  0.3515  0.1255  0.1320  0.3010  0.1425  0.1460  0.0950  0.0540   
2022-03-11  0.3515  0.1315  0.1095  0.0555  0.1645  0.1395  0.1950  0.0870   
2022-03-14  0.3570  0.3190  0.0505  0.2955  0.3045  0.2085  0.3150  0.1250   
2022-03-15  0.1715  0.0765  0.1390  0.1430  0.1755  0.1705  0.1550  0.0465   
2022-03-16  0.3380  0.1165  0.0645  0.1530  0.2755  0.0705  0.2910  0.1265   
2022-03-17  0.3335  0.1790  0.4105  0.0850  0.1045  0.1050  0.2910  0.1410   
2022-03-18  0.3230  0.1530  0.0845  

In [ ]:
RPS_1m.mean(axis=1)

date
2022-01-06    0.166533
2022-01-07    0.176622
2022-01-10    0.152978
2022-01-11    0.148978
2022-01-12    0.175578
2022-01-13    0.165067
2022-01-14    0.151711
2022-01-18    0.138867
2022-01-19    0.160089
2022-01-20    0.158667
2022-01-21    0.145689
2022-01-24    0.200111
2022-01-25    0.144644
2022-01-26    0.164622
2022-01-27    0.168867
2022-01-28    0.170356
2022-01-31    0.157244
2022-02-01    0.157178
2022-02-02    0.154711
2022-02-03    0.166933
2022-02-04    0.179089
2022-02-07    0.151378
2022-02-08    0.151889
2022-02-09    0.161467
2022-02-10    0.172956
2022-02-11    0.179311
2022-02-14    0.157044
2022-02-15    0.172622
2022-02-16    0.163622
2022-02-17    0.155733
2022-02-18    0.167644
2022-02-22    0.158022
2022-02-23    0.160378
2022-02-24    0.181222
2022-02-25    0.180933
2022-02-28    0.148533
2022-03-01    0.154844
2022-03-02    0.169689
2022-03-03    0.191244
2022-03-04    0.152511
2022-03-07    0.134133
2022-03-08    0.148333
2022-03-09    0.151911
2022-0

In [ ]:
RPS_1m.mean(axis=1).mean()

0.162642962962963

#####Two Months


In [ ]:
t_2m=pred(q1_1,155)
t_2m=pd.DataFrame.from_dict(t_2m)
t_2m.set_index('date')
RPS_2m= RPS_data(t_2m,rd)
RPS_2m= create_RPS(t_2m,RPS_2m)
RPS_2m
print(RPS_2m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-02-24    5
Name: UNH, dtype: int64 mikos 40
5 defaultdict(<class 'int'>, {3: 12, 2: 10, 1: 3, 4: 8, 5: 7})
imera : 2022-02-28
arxi insample Date
2021-12-30    2
Name: UNH, dtype: int64 kai telos insample Date
2022-02-24    5
2022-02-25    4
Name: UNH, dtype: int64 mikos 40
4 defaultdict(<class 'int'>, {2: 10, 3: 11, 1: 3, 4: 9, 5: 7})
imera : 2022-03-01
arxi insample Date
2021-12-31    3
Name: UNH, dtype: int64 kai telos insample Date
2022-02-25    4
2022-02-28    5
Name: UNH, dtype: int64 mikos 40
5 defaultdict(<class 'int'>, {3: 11, 1: 3, 4: 9, 2: 9, 5: 8})
imera : 2022-03-02
arxi insample Date
2022-01-03    1
Name: UNH, dtype: int64 kai telos insample Date
2022-02-28    5
2022-03-01    3
Name: UNH, dtype: int64 mikos 40
3 defaultdict(<class 'int'>, {1: 3, 4: 9, 2: 9, 5: 8, 3: 11})
imera : 2022-03-03
arxi insample Date
2022-01-04    4
Name: UNH, dtype: int64 kai telos insample Date
2022-03-01    3
2022-03-02    4
Name: UNH, 

In [ ]:
RPS_2m

ABBV       AEP       AIZ      ALLE      AMAT       AMP  \
date                                                                     
2022-01-06  0.180750  0.142125  0.119000  0.078625  0.143875  0.069125   
2022-01-07  0.342500  0.142125  0.279375  0.262750  0.193875  0.073250   
2022-01-10  0.150750  0.148375  0.100750  0.217125  0.210000  0.249125   
2022-01-11  0.090750  0.208375  0.286875  0.085750  0.206625  0.264875   
2022-01-12  0.148125  0.316250  0.116875  0.083625  0.126875  0.135625   
2022-01-13  0.089000  0.329875  0.297375  0.213250  0.213250  0.225625   
2022-01-14  0.149000  0.157750  0.304250  0.204500  0.193750  0.215500   
2022-01-18  0.087750  0.202125  0.134250  0.131375  0.143250  0.275625   
2022-01-19  0.190375  0.080250  0.051375  0.081375  0.213250  0.227250   
2022-01-20  0.143250  0.210250  0.152250  0.083250  0.213250  0.072875   
2022-01-21  0.149625  0.064375  0.152250  0.231750  0.123500  0.078375   
2022-01-24  0.332750  0.075250  0.049625  0.117250  0.216875  0.134750   
2022-01-25  0.106375  0.075250  0.132500  0.127750  0.136875  0.229500   
2022-01-26  0.192500  0.190125  0.291500  0.083125  0.136875  0.073875   
2022-01-27  0.092500  0.065250  0.096250  0.257125  0.135125  0.273875   
2022-01-28  0.183250  0.177625  0.052375  0.129250  0.167625  0.229125   
2022-01-31  0.093250  0.187625  0.296250  0.134250  0.206875  0.079125   
2022-02-01  0.097625  0.204375  0.060375  0.077375  0.206875  0.278500   
2022-02-02  0.102750  0.199500  0.300375  0.079125  0.146625  0.290250   
2022-02-03  0.177250  0.184125  0.059625  0.199125  0.223500  0.076875   
2022-02-04  0.182375  0.326750  0.059375  0.160500  0.153500  0.218625   
2022-02-07  0.092375  0.062375  0.115750  0.208750  0.220125  0.082500   
2022-02-08  0.156750  0.069625  0.274875  0.088750  0.120375  0.072500   
2022-02-09  0.166125  0.157375  0.059625  0.083750  0.251625  0.079875   
2022-02-10  0.106125  0.145625  0.063250  0.145875  0.193750  0.067125   
2022-02-11  0.152750  0.295625  0.124250  0.085875  0.213250  0.204375   
2022-02-14  0.106125  0.275750  0.068625  0.082500  0.115750  0.077250   
2022-02-15  0.096125  0.261250  0.141250  0.092500  0.205750  0.094500   
2022-02-16  0.106125  0.108875  0.204625  0.092500  0.149125  0.187500   
2022-02-17  0.166750  0.089625  0.074625  0.085875  0.145750  0.194500   
2022-02-18  0.091875  0.210625  0.071750  0.211250  0.203500  0.094500   
2022-02-22  0.095250  0.152875  0.194250  0.207875  0.244500  0.199125   
2022-02-23  0.103750  0.159500  0.077250  0.191750  0.177750  0.084000   
2022-02-24  0.104625  0.087375  0.361875  0.160125  0.116250  0.292125   
2022-02-25  0.319750  0.092750  0.361875  0.078750  0.164375  0.176500   
2022-02-28  0.175125  0.184875  0.063750  0.094125  0.191250  0.082250   
2022-03-01  0.106125  0.180500  0.199125  0.194125  0.191250  0.313875   
2022-03-02  0.099750  0.183875  0.204250  0.140500  0.188625  0.316250   
2022-03-03  0.161000  0.172125  0.346125  0.070500  0.158625  0.078750   
2022-03-04  0.172750  0.072125  0.061500  0.106375  0.188625  0.078375   
2022-03-07  0.164250  0.157500  0.075875  0.230375  0.097750  0.268750   
2022-03-08  0.167625  0.322125  0.059125  0.132500  0.255750  0.264375   
2022-03-09  0.103250  0.167125  0.056625  0.232250  0.204750  0.101125   
2022-03-10  0.314500  0.118250  0.191250  0.284875  0.188625  0.104375   
2022-03-11  0.322750  0.168250  0.066375  0.064875  0.182625  0.154375   
2022-03-14  0.347250  0.313375  0.064750  0.281250  0.275750  0.220250   
2022-03-15  0.153875  0.081375  0.174750  0.131250  0.175750  0.150250   
2022-03-16  0.328750  0.111250  0.066375  0.127875  0.253750  0.071750   
2022-03-17  0.340750  0.131875  0.386375  0.127875  0.096250  0.091625   
2022-03-18  0.347625  0.123250  0.066375  0.275500  0.125750  0.071625   
2022-03-21  0.157625  0.111125  0.203875  0.134625  0.125750  0.310000   
2022-03-22  0.077625  0.224625  0.163875  0.310875  0.093125  0.317250   
2022-03-23  0.079375

In [ ]:
RPS_2m.mean(axis=1)

date
2022-01-06    0.169656
2022-01-07    0.169122
2022-01-10    0.165000
2022-01-11    0.146894
2022-01-12    0.172044
2022-01-13    0.176672
2022-01-14    0.155594
2022-01-18    0.139400
2022-01-19    0.158917
2022-01-20    0.160644
2022-01-21    0.145261
2022-01-24    0.181722
2022-01-25    0.148689
2022-01-26    0.168306
2022-01-27    0.161128
2022-01-28    0.164839
2022-01-31    0.149522
2022-02-01    0.152256
2022-02-02    0.153867
2022-02-03    0.170050
2022-02-04    0.173189
2022-02-07    0.150322
2022-02-08    0.151994
2022-02-09    0.160983
2022-02-10    0.171122
2022-02-11    0.174594
2022-02-14    0.159078
2022-02-15    0.175994
2022-02-16    0.152733
2022-02-17    0.165950
2022-02-18    0.150594
2022-02-22    0.164806
2022-02-23    0.147489
2022-02-24    0.187761
2022-02-25    0.185706
2022-02-28    0.138806
2022-03-01    0.153722
2022-03-02    0.165544
2022-03-03    0.185017
2022-03-04    0.147672
2022-03-07    0.139172
2022-03-08    0.149522
2022-03-09    0.147417
2022-0

In [ ]:
RPS_2m.mean(axis=1).mean()

0.16090648148148146

#####3 months

In [ ]:
t_3m=pred(q1_1,135)
t_3m=pd.DataFrame.from_dict(t_3m)
t_3m.set_index('date')
RPS_3m= RPS_data(t_3m,rd)
RPS_3m= create_RPS(t_3m,RPS_3m)
RPS_3m
print(RPS_3m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-02-24    5
Name: UNH, dtype: int64 mikos 60
5 defaultdict(<class 'int'>, {4: 17, 1: 4, 3: 15, 5: 11, 2: 13})
imera : 2022-02-28
arxi insample Date
2021-12-01    1
Name: UNH, dtype: int64 kai telos insample Date
2022-02-24    5
2022-02-25    4
Name: UNH, dtype: int64 mikos 60
4 defaultdict(<class 'int'>, {1: 4, 4: 17, 3: 15, 5: 11, 2: 13})
imera : 2022-03-01
arxi insample Date
2021-12-02    4
Name: UNH, dtype: int64 kai telos insample Date
2022-02-25    4
2022-02-28    5
Name: UNH, dtype: int64 mikos 60
5 defaultdict(<class 'int'>, {4: 17, 3: 15, 5: 12, 2: 13, 1: 3})
imera : 2022-03-02
arxi insample Date
2021-12-03    4
Name: UNH, dtype: int64 kai telos insample Date
2022-02-28    5
2022-03-01    3
Name: UNH, dtype: int64 mikos 60
3 defaultdict(<class 'int'>, {4: 16, 3: 16, 5: 12, 2: 13, 1: 3})
imera : 2022-03-03
arxi insample Date
2021-12-06    3
Name: UNH, dtype: int64 kai telos insample Date
2022-03-01    3
2022-03-02    4
N

In [ ]:
RPS_3m

ABBV       AEP       AIZ      ALLE      AMAT       AMP  \
date                                                                     
2022-01-06  0.140111  0.131500  0.143889  0.089444  0.119167  0.072222   
2022-01-07  0.304500  0.131500  0.303500  0.249111  0.157056  0.073000   
2022-01-10  0.182722  0.135167  0.085444  0.229000  0.260111  0.229944   
2022-01-11  0.105000  0.235167  0.309167  0.088056  0.267667  0.289944   
2022-01-12  0.182111  0.289056  0.145444  0.088167  0.134333  0.144167   
2022-01-13  0.082722  0.290333  0.315167  0.226778  0.166778  0.229889   
2022-01-14  0.174500  0.143667  0.315167  0.220444  0.155222  0.229889   
2022-01-18  0.103333  0.223667  0.148500  0.118833  0.183722  0.290722   
2022-01-19  0.156667  0.099611  0.065444  0.081944  0.255389  0.237444   
2022-01-20  0.169389  0.213000  0.144389  0.081944  0.250778  0.070778   
2022-01-21  0.173889  0.063889  0.140500  0.235889  0.135389  0.074111   
2022-01-24  0.316167  0.095667  0.060500  0.110167  0.168722  0.131167   
2022-01-25  0.091667  0.091833  0.140000  0.110167  0.167500  0.254167   
2022-01-26  0.151667  0.208111  0.298889  0.080667  0.170111  0.070333   
2022-01-27  0.101500  0.084500  0.093056  0.257944  0.162556  0.264500   
2022-01-28  0.156056  0.153111  0.059722  0.126111  0.143556  0.251889   
2022-01-31  0.109222  0.206444  0.313333  0.122000  0.226056  0.071889   
2022-02-01  0.089222  0.206444  0.060000  0.076000  0.220500  0.259000   
2022-02-02  0.106944  0.206444  0.309667  0.076000  0.151444  0.266333   
2022-02-03  0.162833  0.161556  0.055667  0.211278  0.207722  0.072333   
2022-02-04  0.170611  0.310167  0.054500  0.138889  0.149167  0.238500   
2022-02-07  0.097278  0.082111  0.118667  0.214611  0.220333  0.075833   
2022-02-08  0.159333  0.081389  0.292000  0.101278  0.118167  0.092778   
2022-02-09  0.159944  0.154111  0.052389  0.081278  0.218167  0.072778   
2022-02-10  0.096889  0.145056  0.052389  0.134611  0.211500  0.088056   
2022-02-11  0.185000  0.320778  0.113000  0.077944  0.224944  0.228333   
2022-02-14  0.091667  0.305667  0.053000  0.075667  0.113167  0.093833   
2022-02-15  0.098333  0.295222  0.116111  0.095667  0.219833  0.075000   
2022-02-16  0.091000  0.093278  0.256944  0.093556  0.146611  0.150500   
2022-02-17  0.194611  0.074444  0.109444  0.079444  0.131333  0.217444   
2022-02-18  0.103778  0.215222  0.109444  0.215000  0.219833  0.081889   
2022-02-22  0.109889  0.150833  0.255722  0.215000  0.222000  0.206389   
2022-02-23  0.112500  0.147667  0.058333  0.203833  0.217000  0.089833   
2022-02-24  0.113222  0.077500  0.302333  0.136500  0.110333  0.285222   
2022-02-25  0.340333  0.080778  0.305056  0.074556  0.146611  0.151889   
2022-02-28  0.149722  0.192222  0.086667  0.105500  0.204889  0.078556   
2022-03-01  0.090444  0.187000  0.235389  0.218833  0.209611  0.272167   
2022-03-02  0.099944  0.197500  0.235389  0.132167  0.212333  0.286722   
2022-03-03  0.173278  0.162389  0.312611  0.072167  0.147611  0.078000   
2022-03-04  0.150611  0.072111  0.063889  0.108056  0.194833  0.076667   
2022-03-07  0.147444  0.170778  0.079389  0.225778  0.118111  0.271278   
2022-03-08  0.157056  0.326167  0.063000  0.133833  0.230778  0.275889   
2022-03-09  0.093667  0.165444  0.060778  0.222778  0.210444  0.093778   
2022-03-10  0.327000  0.098778  0.210500  0.280333  0.210444  0.091833   
2022-03-11  0.327000  0.178778  0.068167  0.073667  0.207611  0.168333   
2022-03-14  0.327000  0.302500  0.072833  0.280333  0.241500  0.203667   
2022-03-15  0.167000  0.088056  0.199500  0.107000  0.207611  0.166833   
2022-03-16  0.322611  0.098167  0.066167  0.109444  0.227611  0.084944   
2022-03-17  0.320556  0.136944  0.357889  0.125444  0.111556  0.078556   
2022-03-18  0.331111  0.136944  0.076333  0.274722  0.124889  0.080333   
2022-03-21  0.175833  0.091056  0.172500  0.128056  0.121389  0.290833   
2022-03-22  0.094833  0.200833  0.187611  0.279111  0.112778  0.292222   
2022-03-23  0.094833

In [ ]:
RPS_3m.mean(axis=1)

date
2022-01-06    0.163874
2022-01-07    0.164852
2022-01-10    0.162625
2022-01-11    0.152798
2022-01-12    0.167686
2022-01-13    0.172464
2022-01-14    0.156133
2022-01-18    0.144630
2022-01-19    0.156763
2022-01-20    0.162027
2022-01-21    0.150089
2022-01-24    0.171914
2022-01-25    0.151037
2022-01-26    0.167131
2022-01-27    0.152578
2022-01-28    0.169047
2022-01-31    0.148415
2022-02-01    0.145484
2022-02-02    0.148973
2022-02-03    0.170193
2022-02-04    0.170096
2022-02-07    0.153123
2022-02-08    0.156570
2022-02-09    0.156696
2022-02-10    0.167694
2022-02-11    0.176331
2022-02-14    0.160711
2022-02-15    0.172254
2022-02-16    0.151185
2022-02-17    0.168212
2022-02-18    0.150528
2022-02-22    0.161405
2022-02-23    0.151398
2022-02-24    0.178909
2022-02-25    0.175756
2022-02-28    0.143780
2022-03-01    0.151005
2022-03-02    0.161958
2022-03-03    0.176415
2022-03-04    0.142689
2022-03-07    0.138336
2022-03-08    0.147973
2022-03-09    0.146617
2022-0

In [ ]:
RPS_3m.mean(axis=1).mean()

0.15917917695473252

#####6 months

In [ ]:
t_6m=pred(q1_1,75)
t_6m=pd.DataFrame.from_dict(t_6m)
t_6m.set_index('date')
RPS_6m= RPS_data(t_6m,rd)
RPS_6m= create_RPS(t_6m,RPS_6m)
RPS_6m
print(RPS_6m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-02-24    5
Name: UNH, dtype: int64 mikos 120
5 defaultdict(<class 'int'>, {4: 25, 1: 13, 3: 31, 5: 27, 2: 24})
imera : 2022-02-28
arxi insample Date
2021-09-07    1
Name: UNH, dtype: int64 kai telos insample Date
2022-02-24    5
2022-02-25    4
Name: UNH, dtype: int64 mikos 120
4 defaultdict(<class 'int'>, {1: 13, 3: 31, 5: 27, 4: 25, 2: 24})
imera : 2022-03-01
arxi insample Date
2021-09-08    3
Name: UNH, dtype: int64 kai telos insample Date
2022-02-25    4
2022-02-28    5
Name: UNH, dtype: int64 mikos 120
5 defaultdict(<class 'int'>, {3: 31, 1: 12, 5: 28, 4: 25, 2: 24})
imera : 2022-03-02
arxi insample Date
2021-09-09    1
Name: UNH, dtype: int64 kai telos insample Date
2022-02-28    5
2022-03-01    3
Name: UNH, dtype: int64 mikos 120
3 defaultdict(<class 'int'>, {1: 12, 5: 28, 4: 25, 3: 31, 2: 24})
imera : 2022-03-03
arxi insample Date
2021-09-10    5
Name: UNH, dtype: int64 kai telos insample Date
2022-03-01    3
2022-03-0

In [ ]:
RPS_6m

ABBV       AEP       AIZ      ALLE      AMAT       AMP  \
date                                                                     
2022-01-06  0.139847  0.116264  0.121361  0.083750  0.121917  0.080167   
2022-01-07  0.288292  0.119514  0.276194  0.256542  0.175819  0.079458   
2022-01-10  0.207153  0.120958  0.103208  0.229139  0.247583  0.213903   
2022-01-11  0.100125  0.248250  0.275250  0.081764  0.249236  0.297931   
2022-01-12  0.209028  0.241583  0.121708  0.081250  0.128819  0.142833   
2022-01-13  0.072819  0.241583  0.283028  0.233903  0.176833  0.206167   
2022-01-14  0.206917  0.117653  0.288250  0.236583  0.170833  0.203306   
2022-01-18  0.100250  0.248917  0.127153  0.113250  0.166833  0.295861   
2022-01-19  0.143583  0.115611  0.056083  0.078569  0.247819  0.215194   
2022-01-20  0.206458  0.241736  0.130764  0.079194  0.240625  0.078528   
2022-01-21  0.203514  0.072333  0.129417  0.239736  0.129167  0.078597   
2022-01-24  0.293514  0.114194  0.055833  0.113611  0.182944  0.137417   
2022-01-25  0.075792  0.114194  0.122306  0.112958  0.159167  0.216264   
2022-01-26  0.153750  0.240861  0.285639  0.078250  0.162944  0.075639   
2022-01-27  0.091361  0.110972  0.099542  0.248250  0.162028  0.285639   
2022-01-28  0.158028  0.124194  0.055139  0.115569  0.132028  0.222403   
2022-01-31  0.094597  0.240861  0.298458  0.115569  0.245861  0.075736   
2022-02-01  0.077500  0.242778  0.055458  0.080931  0.250167  0.279069   
2022-02-02  0.095139  0.239528  0.307542  0.082306  0.169569  0.279069   
2022-02-03  0.151806  0.126194  0.053472  0.226403  0.175875  0.075736   
2022-02-04  0.150986  0.244125  0.053472  0.123069  0.127528  0.219431   
2022-02-07  0.094319  0.114125  0.135819  0.227750  0.256931  0.077139   
2022-02-08  0.197250  0.115417  0.302153  0.112528  0.128639  0.088917   
2022-02-09  0.200542  0.118125  0.052139  0.083069  0.258639  0.074083   
2022-02-10  0.098028  0.114819  0.052417  0.123069  0.171972  0.086306   
2022-02-11  0.149514  0.241403  0.096042  0.083069  0.177972  0.209569   
2022-02-14  0.095208  0.241403  0.053722  0.081208  0.126625  0.091806   
2022-02-15  0.078542  0.238722  0.097375  0.110042  0.174528  0.075139   
2022-02-16  0.096083  0.122083  0.284139  0.108931  0.169125  0.146236   
2022-02-17  0.156181  0.078694  0.127472  0.085597  0.127528  0.215597   
2022-02-18  0.079014  0.240042  0.126208  0.213792  0.248486  0.076236   
2022-02-22  0.079917  0.122069  0.285861  0.212042  0.178486  0.211361   
2022-02-23  0.080972  0.120042  0.052361  0.206417  0.252847  0.090292   
2022-02-24  0.081347  0.081417  0.262361  0.135958  0.129125  0.291361   
2022-02-25  0.311347  0.081500  0.263458  0.082625  0.127528  0.149181   
2022-02-28  0.180972  0.228333  0.117056  0.103681  0.246014  0.075847   
2022-03-01  0.094306  0.231014  0.277139  0.210806  0.248417  0.292972   
2022-03-02  0.080625  0.232306  0.275931  0.130583  0.247208  0.293681   
2022-03-03  0.158861  0.129194  0.269583  0.080125  0.130069  0.075972   
2022-03-04  0.180625  0.102861  0.051764  0.107931  0.233042  0.075958   
2022-03-07  0.178861  0.216903  0.113319  0.222458  0.145139  0.284208   
2022-03-08  0.181667  0.269694  0.051847  0.129597  0.199597  0.281986   
2022-03-09  0.097861  0.133028  0.050750  0.217500  0.228472  0.094208   
2022-03-10  0.311194  0.082792  0.258597  0.278264  0.228472  0.096028   
2022-03-11  0.313694  0.212792  0.052500  0.078458  0.232722  0.149292   
2022-03-14  0.313694  0.276125  0.105833  0.279597  0.200347  0.204431   
2022-03-15  0.177208  0.098972  0.252500  0.107500  0.230347  0.150389   
2022-03-16  0.318278  0.082306  0.052181  0.106264  0.198139  0.073722   
2022-03-17  0.319875  0.136125  0.287208  0.127458  0.119931  0.089708   
2022-03-18  0.318278  0.136639  0.110431  0.278861  0.147750  0.070875   
2022-03-21  0.180653  0.099264  0.122042  0.128861  0.146792  0.290875   
2022-03-22  0.095917  0.220403  0.255375  0.278861  0.119306  0.295361   
2022-03-23  0.096806

In [ ]:
RPS_6m.mean(axis=1)

date
2022-01-06    0.159185
2022-01-07    0.160127
2022-01-10    0.161706
2022-01-11    0.156440
2022-01-12    0.164986
2022-01-13    0.161770
2022-01-14    0.155342
2022-01-18    0.154073
2022-01-19    0.157566
2022-01-20    0.160115
2022-01-21    0.153656
2022-01-24    0.164551
2022-01-25    0.156031
2022-01-26    0.165171
2022-01-27    0.155922
2022-01-28    0.159760
2022-01-31    0.154266
2022-02-01    0.151678
2022-02-02    0.153994
2022-02-03    0.161681
2022-02-04    0.161276
2022-02-07    0.157554
2022-02-08    0.159973
2022-02-09    0.158315
2022-02-10    0.159683
2022-02-11    0.161341
2022-02-14    0.156356
2022-02-15    0.161906
2022-02-16    0.154933
2022-02-17    0.165060
2022-02-18    0.150874
2022-02-22    0.161047
2022-02-23    0.151541
2022-02-24    0.166544
2022-02-25    0.169040
2022-02-28    0.148089
2022-03-01    0.157662
2022-03-02    0.161981
2022-03-03    0.169568
2022-03-04    0.146770
2022-03-07    0.146151
2022-03-08    0.150108
2022-03-09    0.149437
2022-0

In [ ]:
RPS_6m.mean(axis=1).mean()

0.15833080246913583

#####All the samples

In [ ]:
t_all=pred2(q1_1)
t_all=pd.DataFrame.from_dict(t_all)
t_all.set_index('date')
RPS_all= RPS_data(t_all,rd)
RPS_all= create_RPS(t_all,RPS_all)
RPS_all
print(RPS_all.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
[datetime.date(2022, 1, 7), datetime.date(2022, 1, 10), datetime.date(2022, 1, 11), datetime.date(2022, 1, 12), datetime.date(2022, 1, 13), datetime.date(2022, 1, 14), datetime.date(2022, 1, 18), datetime.date(2022, 1, 19), datetime.date(2022, 1, 20), datetime.date(2022, 1, 21), datetime.date(2022, 1, 24), datetime.date(2022, 1, 25), datetime.date(2022, 1, 26), datetime.date(2022, 1, 27), datetime.date(2022, 1, 28), datetime.date(2022, 1, 31), datetime.date(2022, 2, 1), datetime.date(2022, 2, 2), datetime.date(2022, 2, 3), datetime.date(2022, 2, 4), datetime.date(2022, 2, 7), datetime.date(2022, 2, 8), datetime.date(2022, 2, 9), datetime.date(2022, 2, 10), datetime.date(2022, 2, 11), datetime.date(2022, 2, 14), datetime.date(2022, 2, 15), datetime.date(2022, 2, 16), datetime.date(2022, 2, 17), datetime.date(2022, 2, 18), datetime.date(2022, 2, 22), datetime.date(2022, 2, 23), datetime.date(2022, 2, 24), datetime.date(2022, 2, 25), 

In [ ]:
RPS_all

ABBV       AEP       AIZ      ALLE      AMAT       AMP  \
date                                                                     
2022-01-07  0.280896  0.111494  0.271405  0.252790  0.208981  0.075252   
2022-01-10  0.210677  0.111579  0.105604  0.235556  0.220513  0.228329   
2022-01-11  0.097657  0.261844  0.273110  0.081685  0.221751  0.277025   
2022-01-12  0.212507  0.236543  0.116875  0.081739  0.120075  0.128913   
2022-01-13  0.076686  0.238078  0.275355  0.235333  0.208647  0.224727   
2022-01-14  0.211914  0.113664  0.275665  0.234625  0.206555  0.224105   
2022-01-18  0.097800  0.256500  0.117975  0.123830  0.142405  0.277590   
2022-01-19  0.140393  0.117324  0.061360  0.081018  0.220198  0.227074   
2022-01-20  0.212273  0.254779  0.118959  0.081433  0.218023  0.075081   
2022-01-21  0.211726  0.072965  0.119057  0.235434  0.120692  0.075333   
2022-01-24  0.279614  0.116513  0.061029  0.123231  0.211217  0.127537   
2022-01-25  0.078192  0.115379  0.116745  0.124059  0.139855  0.229968   
2022-01-26  0.140871  0.252126  0.273098  0.081313  0.141059  0.073989   
2022-01-27  0.097641  0.113160  0.105305  0.254442  0.140293  0.275428   
2022-01-28  0.141984  0.117816  0.061233  0.125162  0.139996  0.228555   
2022-01-31  0.098803  0.253534  0.275749  0.125134  0.218695  0.074824   
2022-02-01  0.078617  0.254980  0.061560  0.080567  0.218984  0.274943   
2022-02-02  0.099674  0.254172  0.277092  0.080636  0.141461  0.276014   
2022-02-03  0.140668  0.117818  0.061076  0.230109  0.211828  0.075040   
2022-02-04  0.141423  0.243475  0.061178  0.127342  0.137975  0.227274   
2022-02-07  0.097738  0.113765  0.116683  0.232697  0.220801  0.075622   
2022-02-08  0.207321  0.114553  0.274670  0.105657  0.117746  0.098176   
2022-02-09  0.208758  0.115338  0.061021  0.080834  0.223637  0.074228   
2022-02-10  0.099004  0.114277  0.061169  0.126390  0.210521  0.097734   
2022-02-11  0.142135  0.243780  0.107348  0.080486  0.212213  0.225368   
2022-02-14  0.097625  0.241559  0.061588  0.079752  0.117554  0.099539   
2022-02-15  0.079545  0.239368  0.109178  0.105607  0.210603  0.075335   
2022-02-16  0.097267  0.118315  0.264945  0.104994  0.142638  0.132806   
2022-02-17  0.145041  0.076090  0.110997  0.080521  0.135951  0.223752   
2022-02-18  0.080066  0.253699  0.111118  0.230473  0.220447  0.076458   
2022-02-22  0.080588  0.115725  0.263700  0.230875  0.213126  0.222206   
2022-02-23  0.081114  0.115761  0.062040  0.228828  0.218765  0.099105   
2022-02-24  0.081251  0.075801  0.270342  0.127250  0.117742  0.276842   
2022-02-25  0.286705  0.075845  0.271315  0.079435  0.137752  0.132791   
2022-02-28  0.203236  0.248103  0.107575  0.106810  0.218994  0.074861   
2022-03-01  0.097119  0.247402  0.261193  0.232726  0.218310  0.275944   
2022-03-02  0.080420  0.248420  0.261527  0.124216  0.219369  0.277255   
2022-03-03  0.143719  0.119001  0.273121  0.078987  0.138686  0.074864   
2022-03-04  0.203961  0.111396  0.061333  0.109342  0.215603  0.075074   
2022-03-07  0.203529  0.242064  0.107171  0.235576  0.135125  0.272718   
2022-03-08  0.204610  0.249916  0.061151  0.124165  0.216524  0.272942   
2022-03-09  0.097601  0.119283  0.060632  0.234600  0.217565  0.101465   
2022-03-10  0.286606  0.077625  0.257379  0.258040  0.215725  0.101566   
2022-03-11  0.287910  0.243074  0.061119  0.078435  0.216009  0.132778   
2022-03-14  0.289210  0.249110  0.105985  0.259290  0.219239  0.223505   
2022-03-15  0.201408  0.112004  0.255916  0.108731  0.215735  0.133447   
2022-03-16  0.289132  0.078007  0.060194  0.108788  0.215601  0.074465   
2022-03-17  0.290026  0.117329  0.277123  0.123786  0.116296  0.098642   
2022-03-18  0.290148  0.116666  0.107728  0.260016  0.138068  0.073960   
2022-03-21  0.202144  0.114068  0.116927  0.125171  0.136934  0.278040   
2022-03-22  0.094985  0.248525  0.255355  0.261230  0.116135  0.279273   
2022-03-23  0.095087  0.078337  0.060411  0.076358  0.138442  0.073749   
2022-03-24  0.204134

In [ ]:
RPS_all.mean(axis=1)

date
2022-01-07    0.156713
2022-01-10    0.161527
2022-01-11    0.156879
2022-01-12    0.161849
2022-01-13    0.160952
2022-01-14    0.156640
2022-01-18    0.156232
2022-01-19    0.157484
2022-01-20    0.159467
2022-01-21    0.156288
2022-01-24    0.159355
2022-01-25    0.157025
2022-01-26    0.161843
2022-01-27    0.158535
2022-01-28    0.159151
2022-01-31    0.155936
2022-02-01    0.156337
2022-02-02    0.156760
2022-02-03    0.157699
2022-02-04    0.159829
2022-02-07    0.157223
2022-02-08    0.158600
2022-02-09    0.157257
2022-02-10    0.158826
2022-02-11    0.159384
2022-02-14    0.158285
2022-02-15    0.158453
2022-02-16    0.156112
2022-02-17    0.159113
2022-02-18    0.155624
2022-02-22    0.161085
2022-02-23    0.155179
2022-02-24    0.161019
2022-02-25    0.161383
2022-02-28    0.154165
2022-03-01    0.159750
2022-03-02    0.162038
2022-03-03    0.162474
2022-03-04    0.153174
2022-03-07    0.153956
2022-03-08    0.155807
2022-03-09    0.154044
2022-03-10    0.162866
2022-0

In [ ]:
RPS_all.mean(axis=1).mean()

0.15829552209923756

####**For 1 May-29 May**

#####Prepare the dataset with the dummy data 

In [ ]:
#cut the dataset(with the ranks) we have until 1 May 
q1_1=rd3.copy()
q1_1=q1_1.loc[(q1_1.index<='2022-05-01') & (q1_1.index>'2021-05-01')]
q1_1

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-05-03     2    2    3     5     1    3     1    2    4    3  ...    4   
2021-05-04     5    2    4     2     4    5     1    1    4    4  ...    5   
2021-05-05     2    3    4     5     4    3     4    5    5    2  ...    4   
2021-05-06     1    1    1     3     4    4     1    4    2    4  ...    2   
2021-05-07     4    4    2     5     1    2     1    4    3    2  ...    4   
...          ...  ...  ...   ...   ...  ...   ...  ...  ...  ...  ...  ...   
2022-04-25     5    4    4     5     1    1     1    4    5    2  ...    2   
2022-04-26     4    3    4     5     3    4     2    1    5    2  ...    4   
2022-04-27     1    4    2     4     5    4     5    1    2    3  ...    2   
2022-04-28     1    2    4     1     2    4     1    1    5    2  ...    3   
2022-04-29     4    2    3     4     5    4     3    1    2    1  ...    3   

            PYPL  RE  ROL  ROST  UNH  URI  V  VRSK  XOM  
Date                                                     
2021-05-03     1   4    2     3    5    5  3     4    4  
2021-05-04     2   3    1     1    3    4  1     1    5  
2021-05-05     5   1    1     2    3    5  3     4    3  
2021-05-06     3   2    3     5    3    4  2     5    4  
2021-05-07     1   3    4     1    5    3  1     4    4  
...          ...  ..  ...   ...  ...  ... ..   ...  ...  
2022-04-25     1   3    3     3    3    2  1     3    5  
2022-04-26     1   5    5     1    3    5  5     3    5  
2022-04-27     5   1    4     4    3    4  5     3    4  
2022-04-28     1   3    4     1    3    5  2     2    4  
2022-04-29     5   4    2     5    1    1  2     2    4  

[252 rows x 45 columns]

In [ ]:
#May '21
#save the values of the month
# may_21 = rd3.loc[(rd3.index <= '2021-05-31') & (rd3.index >= '2021-05-01')]
# may_21

In [ ]:
#may 22
# may_22 = rd3.loc[(rd3.index >= '2022-05-01') & (rd3.index < '2022-05-31')]
# may_22

In [ ]:
# for i in may_22:
#   may_22[i] = may_21[i].values
# may_22

In [ ]:
#now that we have the new "dummy" month all we have to do is to join it with the original dataframe
# q1_1 = pd.concat([q1_1,may_22])
# q1_1

#####15 days

In [ ]:
t_15d=pred(q1_1,179)
t_15d=pd.DataFrame.from_dict(t_15d)
t_15d.set_index('date')
RPS_15d= RPS_data(t_15d,rd)
RPS_15d= create_RPS(t_15d,RPS_15d)
RPS_15d
print(RPS_15d.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-03-23    5
Name: UNH, dtype: int64 mikos 15
5 defaultdict(<class 'int'>, {5: 3, 3: 3, 1: 4, 2: 1, 4: 4})
imera : 2022-03-25
arxi insample Date
2022-03-04    3
Name: UNH, dtype: int64 kai telos insample Date
2022-03-23    5
2022-03-24    1
Name: UNH, dtype: int64 mikos 15
1 defaultdict(<class 'int'>, {3: 3, 1: 5, 5: 2, 2: 1, 4: 4})
imera : 2022-03-28
arxi insample Date
2022-03-07    1
Name: UNH, dtype: int64 kai telos insample Date
2022-03-24    1
2022-03-25    2
Name: UNH, dtype: int64 mikos 15
2 defaultdict(<class 'int'>, {1: 5, 3: 2, 5: 2, 2: 2, 4: 4})
imera : 2022-03-29
arxi insample Date
2022-03-08    3
Name: UNH, dtype: int64 kai telos insample Date
2022-03-25    2
2022-03-28    1
Name: UNH, dtype: int64 mikos 15
1 defaultdict(<class 'int'>, {3: 2, 5: 2, 2: 2, 4: 4, 1: 5})
imera : 2022-03-30
arxi insample Date
2022-03-09    5
Name: UNH, dtype: int64 kai telos insample Date
2022-03-28    1
2022-03-29    5
Name: UNH, dtype:

In [ ]:
RPS_15d

ABBV       AEP       AIZ      ALLE      AMAT       AMP  \
date                                                                     
2022-02-03  0.151111  0.226667  0.038222  0.162667  0.275556  0.080889   
2022-02-04  0.178667  0.331556  0.038222  0.173333  0.168889  0.267556   
2022-02-07  0.098667  0.051556  0.104889  0.209778  0.176000  0.083556   
2022-02-08  0.178667  0.071111  0.261333  0.108444  0.086222  0.082667   
2022-02-09  0.181333  0.120889  0.062222  0.082667  0.274667  0.058667   
2022-02-10  0.101333  0.094222  0.062222  0.149333  0.194667  0.063111   
2022-02-11  0.181333  0.240889  0.173333  0.068444  0.200889  0.183111   
2022-02-14  0.093333  0.240889  0.080000  0.057778  0.076444  0.069333   
2022-02-15  0.106667  0.195556  0.179556  0.105778  0.186667  0.104000   
2022-02-16  0.093333  0.189333  0.166222  0.100444  0.173333  0.205333   
2022-02-17  0.190222  0.127111  0.054222  0.093333  0.088889  0.181333   
2022-02-18  0.104889  0.280000  0.054222  0.178667  0.274667  0.112000   
2022-02-22  0.119111  0.109333  0.133333  0.178667  0.246222  0.150222   
2022-02-23  0.141333  0.118222  0.122667  0.178667  0.219556  0.096889   
2022-02-24  0.150222  0.104889  0.496000  0.136889  0.092444  0.293333   
2022-02-25  0.361778  0.098667  0.496000  0.064000  0.132444  0.186667   
2022-02-28  0.141333  0.186667  0.037333  0.144889  0.210667  0.081778   
2022-03-01  0.091556  0.186667  0.106667  0.240889  0.187556  0.261333   
2022-03-02  0.104889  0.186667  0.114667  0.104000  0.187556  0.280889   
2022-03-03  0.202667  0.186667  0.461333  0.061333  0.209778  0.094222   
2022-03-04  0.166222  0.072000  0.112000  0.168889  0.143111  0.090667   
2022-03-07  0.166222  0.112000  0.045333  0.288889  0.068444  0.224000   
2022-03-08  0.208000  0.402667  0.095111  0.101333  0.282667  0.240889   
2022-03-09  0.097778  0.229333  0.072000  0.300444  0.169778  0.147556   
2022-03-10  0.293333  0.148444  0.172444  0.247111  0.128889  0.158222   
2022-03-11  0.297778  0.112000  0.072000  0.055111  0.138667  0.152000   
2022-03-14  0.334222  0.392889  0.058667  0.268444  0.352000  0.257778   
2022-03-15  0.194667  0.069333  0.165333  0.160000  0.181333  0.145778   
2022-03-16  0.293333  0.121778  0.049778  0.176000  0.250667  0.068444   
2022-03-17  0.349333  0.136000  0.396444  0.084444  0.101333  0.087111   
2022-03-18  0.349333  0.115556  0.111111  0.280889  0.117333  0.056000   
2022-03-21  0.196444  0.136000  0.164444  0.115556  0.117333  0.275556   
2022-03-22  0.069333  0.271111  0.183111  0.333333  0.104000  0.336000   
2022-03-23  0.061333  0.115556  0.061333  0.048000  0.152000  0.051556   
2022-03-24  0.221333  0.151111  0.074667  0.408000  0.245333  0.336000   
2022-03-25  0.074667  0.112000  0.074667  0.429333  0.112000  0.062222   
2022-03-28  0.343111  0.194667  0.168889  0.207111  0.182222  0.062222   
2022-03-29  0.317333  0.072889  0.097778  0.172444  0.160889  0.066667   
2022-03-30  0.073778  0.090667  0.069333  0.221333  0.233778  0.073778   
2022-03-31  0.073778  0.081778  0.088889  0.074667  0.100444  0.082667   
2022-04-01  0.337778  0.101333  0.168889  0.065778  0.255111  0.230222   
2022-04-04  0.278222  0.154667  0.194667  0.079111  0.218667  0.256889   
2022-04-05  0.107556  0.126222  0.088000  0.061333  0.115556  0.127111   
2022-04-06  0.088889  0.171556  0.186667  0.444444  0.141333  0.064000   
2022-04-07  0.095111  0.158222  0.080000  0.128889  0.288889  0.077333   
2022-04-08  0.080000  0.168889  0.087111  0.072000  0.114667  0.083556   
2022-04-11  0.197333  0.317333  0.207111  0.370667  0.368000  0.186667   
2022-04-12  0.281778  0.165333  0.193778  0.090667  0.418667  0.347556   
2022-04-13  0.216000  0.089778  0.193778  0.104889  0.119111  0.091556   
2022-04-14  0.262222  0.158222  0.087111  0.083556  0.418667  0.360889   
2022-04-18  0.200000  0.163556  0.180444  0.077333  0.119111  0.088000   
2022-04-19  0.141333  0.158222  0.313778  0.077333  0.119111  0.179556   
2022-04-20  0.154667

In [ ]:
RPS_15d.mean(axis=1)

date
2022-02-03    0.174736
2022-02-04    0.180267
2022-02-07    0.151348
2022-02-08    0.158183
2022-02-09    0.166479
2022-02-10    0.162331
2022-02-11    0.163160
2022-02-14    0.158064
2022-02-15    0.164109
2022-02-16    0.179319
2022-02-17    0.153284
2022-02-18    0.172840
2022-02-22    0.163556
2022-02-23    0.155575
2022-02-24    0.198795
2022-02-25    0.196267
2022-02-28    0.146291
2022-03-01    0.154193
2022-03-02    0.165057
2022-03-03    0.200257
2022-03-04    0.142301
2022-03-07    0.125867
2022-03-08    0.151190
2022-03-09    0.155773
2022-03-10    0.177857
2022-03-11    0.143921
2022-03-14    0.179793
2022-03-15    0.143881
2022-03-16    0.158104
2022-03-17    0.175684
2022-03-18    0.179081
2022-03-21    0.172207
2022-03-22    0.175881
2022-03-23    0.154983
2022-03-24    0.180741
2022-03-25    0.163832
2022-03-28    0.150123
2022-03-29    0.174894
2022-03-30    0.171141
2022-03-31    0.164543
2022-04-01    0.172365
2022-04-04    0.181807
2022-04-05    0.173314
2022-0

In [ ]:
RPS_15d.mean(axis=1).mean()

0.16741465020576135

#####One Month (20 working days)

In [ ]:
t_1m=pred(q1_1,174)
t_1m=pd.DataFrame.from_dict(t_1m)
t_1m.set_index('date')
RPS_1m= RPS_data(t_1m,rd)
RPS_1m= create_RPS(t_1m,RPS_1m)
RPS_1m
print(RPS_1m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-03-23    5
Name: UNH, dtype: int64 mikos 20
5 defaultdict(<class 'int'>, {5: 5, 4: 6, 3: 4, 1: 4, 2: 1})
imera : 2022-03-25
arxi insample Date
2022-02-25    4
Name: UNH, dtype: int64 kai telos insample Date
2022-03-23    5
2022-03-24    1
Name: UNH, dtype: int64 mikos 20
1 defaultdict(<class 'int'>, {4: 6, 5: 4, 3: 4, 1: 5, 2: 1})
imera : 2022-03-28
arxi insample Date
2022-02-28    5
Name: UNH, dtype: int64 kai telos insample Date
2022-03-24    1
2022-03-25    2
Name: UNH, dtype: int64 mikos 20
2 defaultdict(<class 'int'>, {5: 4, 3: 4, 4: 5, 1: 5, 2: 2})
imera : 2022-03-29
arxi insample Date
2022-03-01    3
Name: UNH, dtype: int64 kai telos insample Date
2022-03-25    2
2022-03-28    1
Name: UNH, dtype: int64 mikos 20
1 defaultdict(<class 'int'>, {3: 4, 4: 5, 5: 3, 1: 6, 2: 2})
imera : 2022-03-30
arxi insample Date
2022-03-02    4
Name: UNH, dtype: int64 kai telos insample Date
2022-03-28    1
2022-03-29    5
Name: UNH, dtype:

In [ ]:
t_1m

ABBV                            AEP  \
0     [0.1, 0.3, 0.2, 0.05, 0.35]  [0.15, 0.15, 0.05, 0.45, 0.2]   
1     [0.1, 0.25, 0.2, 0.1, 0.35]  [0.15, 0.15, 0.05, 0.45, 0.2]   
2     [0.1, 0.25, 0.15, 0.1, 0.4]  [0.15, 0.15, 0.05, 0.5, 0.15]   
3     [0.1, 0.3, 0.15, 0.1, 0.35]    [0.15, 0.2, 0.0, 0.5, 0.15]   
4   [0.15, 0.25, 0.15, 0.1, 0.35]    [0.1, 0.25, 0.0, 0.5, 0.15]   
5     [0.15, 0.25, 0.1, 0.1, 0.4]    [0.1, 0.3, 0.0, 0.45, 0.15]   
6     [0.1, 0.25, 0.1, 0.15, 0.4]    [0.1, 0.3, 0.0, 0.45, 0.15]   
7     [0.1, 0.25, 0.1, 0.15, 0.4]    [0.15, 0.3, 0.0, 0.4, 0.15]   
8   [0.1, 0.25, 0.15, 0.15, 0.35]    [0.2, 0.3, 0.0, 0.35, 0.15]   
9     [0.1, 0.2, 0.15, 0.15, 0.4]    [0.2, 0.35, 0.0, 0.3, 0.15]   
10    [0.1, 0.15, 0.15, 0.2, 0.4]    [0.2, 0.35, 0.0, 0.25, 0.2]   
11    [0.1, 0.2, 0.15, 0.15, 0.4]    [0.2, 0.35, 0.0, 0.3, 0.15]   
12  [0.1, 0.15, 0.15, 0.15, 0.45]    [0.15, 0.35, 0.0, 0.3, 0.2]   
13  [0.1, 0.15, 0.15, 0.15, 0.45]  [0.15, 0.35, 0.05, 0.25, 0.2]   
14  [0.15, 0.15, 0.15, 0.15, 0.4]  [0.15, 0.35, 0.05, 0.25, 0.2]   
15  [0.15, 0.15, 0.2, 0.15, 0.35]  [0.15, 0.35, 0.05, 0.25, 0.2]   
16  [0.15, 0.2, 0.15, 0.15, 0.35]  [0.15, 0.3, 0.05, 0.25, 0.25]   
17    [0.1, 0.2, 0.15, 0.2, 0.35]  [0.15, 0.25, 0.05, 0.3, 0.25]   
18    [0.1, 0.2, 0.15, 0.2, 0.35]    [0.1, 0.3, 0.05, 0.3, 0.25]   
19    [0.1, 0.2, 0.1, 0.25, 0.35]    [0.1, 0.3, 0.05, 0.25, 0.3]   
20    [0.1, 0.2, 0.15, 0.25, 0.3]    [0.1, 0.3, 0.05, 0.25, 0.3]   
21    [0.1, 0.2, 0.15, 0.25, 0.3]  [0.1, 0.25, 0.05, 0.25, 0.35]   
22  [0.1, 0.25, 0.15, 0.25, 0.25]    [0.1, 0.3, 0.05, 0.2, 0.35]   
23  [0.1, 0.25, 0.15, 0.25, 0.25]  [0.15, 0.25, 0.05, 0.2, 0.35]   
24  [0.05, 0.25, 0.15, 0.3, 0.25]  [0.15, 0.2, 0.05, 0.25, 0.35]   
25  [0.05, 0.25, 0.15, 0.3, 0.25]  [0.15, 0.15, 0.05, 0.3, 0.35]   
26  [0.05, 0.25, 0.15, 0.25, 0.3]    [0.15, 0.2, 0.05, 0.3, 0.3]   
27  [0.05, 0.25, 0.15, 0.3, 0.25]    [0.1, 0.25, 0.05, 0.3, 0.3]   
28    [0.05, 0.3, 0.1, 0.3, 0.25]    [0.1, 0.25, 0.05, 0.3, 0.3]   
29    [0.05, 0.3, 0.1, 0.35, 0.2]    [0.15, 0.2, 0.05, 0.3, 0.3]   
30    [0.05, 0.3, 0.15, 0.3, 0.2]    [0.2, 0.2, 0.05, 0.3, 0.25]   
31  [0.05, 0.25, 0.15, 0.35, 0.2]    [0.2, 0.2, 0.05, 0.3, 0.25]   
32  [0.05, 0.3, 0.15, 0.35, 0.15]      [0.2, 0.2, 0.1, 0.3, 0.2]   
33    [0.05, 0.3, 0.2, 0.35, 0.1]    [0.2, 0.2, 0.05, 0.3, 0.25]   
34    [0.0, 0.3, 0.25, 0.35, 0.1]  [0.2, 0.25, 0.05, 0.25, 0.25]   
35    [0.0, 0.3, 0.25, 0.35, 0.1]    [0.2, 0.3, 0.05, 0.2, 0.25]   
36    [0.0, 0.25, 0.3, 0.35, 0.1]      [0.2, 0.3, 0.1, 0.2, 0.2]   
37    [0.05, 0.25, 0.3, 0.3, 0.1]    [0.2, 0.3, 0.15, 0.15, 0.2]   
38    [0.05, 0.2, 0.3, 0.3, 0.15]  [0.2, 0.25, 0.15, 0.15, 0.25]   
39    [0.05, 0.2, 0.3, 0.3, 0.15]  [0.2, 0.25, 0.15, 0.15, 0.25]   
40    [0.05, 0.2, 0.3, 0.3, 0.15]  [0.2, 0.25, 0.15, 0.15, 0.25]   
41  [0.05, 0.25, 0.3, 0.25, 0.15]    [0.2, 0.3, 0.15, 0.15, 0.2]   
42    [0.05, 0.2, 0.3, 0.25, 0.2]    [0.2, 0.25, 0.15, 0.2, 0.2]   
43  [0.05, 0.15, 0.3, 0.25, 0.25]  [0.15, 0.25, 0.15, 0.2, 0.25]   
44    [0.05, 0.15, 0.3, 0.2, 0.3]  [0.2, 0.25, 0.15, 0.15, 0.25]   
45  [0.05, 0.15, 0.3, 0.25, 0.25]    [0.2, 0.3, 0.15, 0.1, 0.25]   
46    [0.1, 0.15, 0.3, 0.25, 0.2]    [0.2, 0.25, 0.2, 0.1, 0.25]   
47    [0.15, 0.15, 0.3, 0.2, 0.2]      [0.2, 0.2, 0.2, 0.1, 0.3]   
48      [0.2, 0.1, 0.3, 0.2, 0.2]      [0.2, 0.2, 0.2, 0.1, 0.3]   
49    [0.2, 0.1, 0.3, 0.15, 0.25]    [0.15, 0.2, 0.2, 0.15, 0.3]   
50  [0.25, 0.1, 0.25, 0.15, 0.25]    [0.1, 0.2, 0.25, 0.15, 0.3]   
51    [0.3, 0.1, 0.25, 0.1, 0.25]    [0.1, 0.25, 0.25, 0.1, 0.3]   
52  [0.35, 0.05, 0.25, 0.1, 0.25]      [0.1, 0.3, 0.2, 0.1, 0.3]   
53    [0.35, 0.05, 0.2, 0.1, 0.3]    [0.1, 0.3, 0.2, 0.15, 0.25]   
54  [0.35, 0.05, 0.15, 0.15, 0.3]    [0.1, 0.25, 0.2, 0.15, 0.3]   
55    [0.35, 0.05, 0.1, 0.2, 0.3]    [0.1, 0.2, 0.25, 0.15, 0.3]   
56  [0.35, 0.05, 0.05, 0.2, 0.35]      [0.1, 0.2, 0.2, 0.2, 0.3]   
57  [0.3, 0.05, 0.05, 0.25, 0.35]      [0.1, 0.2, 0.2, 0.2, 0.3]   
58  [0.35, 0.05, 

In [ ]:
RPS_1m

ABBV     AEP     AIZ    ALLE    AMAT     AMP    AMZN     AVB  \
date                                                                         
2022-02-03  0.1305  0.1950  0.0485  0.1545  0.2380  0.0830  0.1075  0.1190   
2022-02-04  0.1515  0.3350  0.0465  0.1855  0.1650  0.2230  0.1080  0.0665   
2022-02-07  0.1085  0.0515  0.1395  0.2005  0.2175  0.0855  0.2680  0.0680   
2022-02-08  0.1790  0.0580  0.2970  0.0910  0.0975  0.0655  0.1115  0.0790   
2022-02-09  0.1815  0.1755  0.0450  0.0745  0.2430  0.0725  0.1745  0.1215   
2022-02-10  0.1185  0.1505  0.0450  0.1590  0.2430  0.0750  0.2650  0.2250   
2022-02-11  0.1790  0.3105  0.1495  0.0705  0.2495  0.2355  0.1450  0.1050   
2022-02-14  0.0990  0.2700  0.0580  0.0630  0.0975  0.1135  0.2495  0.0945   
2022-02-15  0.1010  0.2325  0.1710  0.1105  0.2345  0.0745  0.2495  0.1975   
2022-02-16  0.0925  0.1335  0.1660  0.1055  0.1555  0.1795  0.1285  0.0975   
2022-02-17  0.2185  0.1170  0.0530  0.0760  0.1110  0.1885  0.2030  0.1975   
2022-02-18  0.1125  0.2735  0.0530  0.1870  0.2555  0.0955  0.1030  0.1710   
2022-02-22  0.1270  0.1125  0.1530  0.1800  0.2345  0.1555  0.2085  0.0870   
2022-02-23  0.1270  0.1030  0.0930  0.1665  0.2415  0.0755  0.1085  0.2835   
2022-02-24  0.1150  0.1030  0.3770  0.1710  0.0815  0.3105  0.2035  0.1435   
2022-02-25  0.3170  0.1030  0.4245  0.0765  0.1170  0.1705  0.1910  0.2615   
2022-02-28  0.1635  0.2075  0.0415  0.1225  0.2445  0.0825  0.1845  0.2070   
2022-03-01  0.0850  0.1895  0.1415  0.2115  0.2210  0.3010  0.1115  0.0775   
2022-03-02  0.1050  0.1870  0.1390  0.1070  0.2285  0.3075  0.0955  0.2565   
2022-03-03  0.1965  0.1525  0.4780  0.0700  0.1550  0.0790  0.3030  0.2365   
2022-03-04  0.1585  0.0925  0.1045  0.1810  0.1805  0.0825  0.1650  0.0765   
2022-03-07  0.1585  0.1430  0.0510  0.2900  0.0910  0.2460  0.1330  0.2375   
2022-03-08  0.1890  0.3190  0.1110  0.1115  0.2755  0.2330  0.0930  0.2740   
2022-03-09  0.0890  0.1615  0.0985  0.2590  0.1755  0.1460  0.1250  0.0650   
2022-03-10  0.3515  0.1255  0.1320  0.3010  0.1425  0.1460  0.0950  0.0540   
2022-03-11  0.3515  0.1315  0.1095  0.0555  0.1645  0.1395  0.1950  0.0870   
2022-03-14  0.3570  0.3190  0.0505  0.2955  0.3045  0.2085  0.3150  0.1250   
2022-03-15  0.1715  0.0765  0.1390  0.1430  0.1755  0.1705  0.1550  0.0465   
2022-03-16  0.3380  0.1165  0.0645  0.1530  0.2755  0.0705  0.2910  0.1265   
2022-03-17  0.3335  0.1790  0.4105  0.0850  0.1045  0.1050  0.2910  0.1410   
2022-03-18  0.3230  0.1530  0.0845  0.2820  0.1050  0.0570  0.1935  0.2690   
2022-03-21  0.1870  0.0930  0.1975  0.1075  0.0995  0.2895  0.2270  0.2690   
2022-03-22  0.0795  0.2180  0.1775  0.2875  0.0930  0.3015  0.0890  0.3110   
2022-03-23  0.0875  0.1130  0.0575  0.0475  0.1470  0.0615  0.0990  0.2310   
2022-03-24  0.2405  0.1110  0.0725  0.3110  0.2070  0.3310  0.2550  0.1310   
2022-03-25  0.0805  0.1110  0.0830  0.3375  0.1125  0.0855  0.1650  0.2325   
2022-03-28  0.3550  0.1380  0.1730  0.1430  0.2430  0.0935  0.1905  0.2690   
2022-03-29  0.3125  0.0905  0.0945  0.1970  0.1430  0.0900  0.2605  0.2790   
2022-03-30  0.0780  0.1130  0.0630  0.1810  0.2495  0.0970  0.0860  0.2415   
2022-03-31  0.0780  0.0930  0.0830  0.0725  0.1095  0.1060  0.1605  0.0525   
2022-04-01  0.3380  0.1130  0.1980  0.0760  0.2495  0.2260  0.2470  0.2350   
2022-04-04  0.2350  0.1505  0.1900  0.0760  0.2095  0.2970  0.2910  0.1615   
2022-04-05  0.0815  0.1285  0.0700  0.0705  0.1125  0.1570  0.2620  0.2140   
2022-04-06  0.0710  0.2095  0.1795  0.4230  0.1545  0.0550  0.2350  0.1230   
2022-04-07  0.0765  0.1130  0.0900  0.1705  0.2495  0.0660  0.1085  0.1960   
2022-04-08  0.0710  0.2550  0.0570  0.0760  0.1665  0.0660  0.1845  0.2760   
2022-04-11  0.2030  0.2255  0.1700  0.3610  0.2665  0.2335  0.1580  0.0685   
2022-04-12  0.2825  0.1300  0.1700  0.0765  0.3135  0.2735  0.2525  0.0630   
2022-04-13  0.2260  0.0900  0.1950  0.0825  0.1135  0.0735  0.1980  0.1430   
2022-04-14  0.2705  0.1475  0.0710  

In [ ]:
RPS_1m.mean(axis=1)

date
2022-02-03    0.166933
2022-02-04    0.179089
2022-02-07    0.151378
2022-02-08    0.151889
2022-02-09    0.161467
2022-02-10    0.172956
2022-02-11    0.179311
2022-02-14    0.157044
2022-02-15    0.172622
2022-02-16    0.163622
2022-02-17    0.155733
2022-02-18    0.167644
2022-02-22    0.158022
2022-02-23    0.160378
2022-02-24    0.181222
2022-02-25    0.180933
2022-02-28    0.148533
2022-03-01    0.154844
2022-03-02    0.169689
2022-03-03    0.191244
2022-03-04    0.152511
2022-03-07    0.134133
2022-03-08    0.148333
2022-03-09    0.151911
2022-03-10    0.171622
2022-03-11    0.147133
2022-03-14    0.171822
2022-03-15    0.141089
2022-03-16    0.165067
2022-03-17    0.177978
2022-03-18    0.170511
2022-03-21    0.169800
2022-03-22    0.167711
2022-03-23    0.160067
2022-03-24    0.165289
2022-03-25    0.158467
2022-03-28    0.159578
2022-03-29    0.166422
2022-03-30    0.172400
2022-03-31    0.162244
2022-04-01    0.164978
2022-04-04    0.180178
2022-04-05    0.172444
2022-0

In [ ]:
RPS_1m.mean(axis=1).mean()

0.16538148148148146

#####Two Months
***

In [ ]:
t_2m=pred(q1_1,154)
t_2m=pd.DataFrame.from_dict(t_2m)
t_2m.set_index('date')
RPS_2m= RPS_data(t_2m,rd)
RPS_2m= create_RPS(t_2m,RPS_2m)
RPS_2m
print(RPS_2m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-03-23    5
Name: UNH, dtype: int64 mikos 40
5 defaultdict(<class 'int'>, {4: 9, 2: 8, 3: 10, 1: 5, 5: 8})
imera : 2022-03-25
arxi insample Date
2022-01-27    2
Name: UNH, dtype: int64 kai telos insample Date
2022-03-23    5
2022-03-24    1
Name: UNH, dtype: int64 mikos 40
1 defaultdict(<class 'int'>, {2: 8, 3: 10, 1: 6, 5: 8, 4: 8})
imera : 2022-03-28
arxi insample Date
2022-01-28    3
Name: UNH, dtype: int64 kai telos insample Date
2022-03-24    1
2022-03-25    2
Name: UNH, dtype: int64 mikos 40
2 defaultdict(<class 'int'>, {3: 10, 1: 6, 5: 8, 2: 8, 4: 8})
imera : 2022-03-29
arxi insample Date
2022-01-31    1
Name: UNH, dtype: int64 kai telos insample Date
2022-03-25    2
2022-03-28    1
Name: UNH, dtype: int64 mikos 40
1 defaultdict(<class 'int'>, {1: 7, 5: 8, 2: 8, 3: 9, 4: 8})
imera : 2022-03-30
arxi insample Date
2022-02-01    5
Name: UNH, dtype: int64 kai telos insample Date
2022-03-28    1
2022-03-29    5
Name: UNH, dty

In [ ]:
RPS_2m.mean(axis=1)

date
2022-02-03    0.170050
2022-02-04    0.173189
2022-02-07    0.150322
2022-02-08    0.151994
2022-02-09    0.160983
2022-02-10    0.171122
2022-02-11    0.174594
2022-02-14    0.159078
2022-02-15    0.175994
2022-02-16    0.152733
2022-02-17    0.165950
2022-02-18    0.150594
2022-02-22    0.164806
2022-02-23    0.147489
2022-02-24    0.187761
2022-02-25    0.185706
2022-02-28    0.138806
2022-03-01    0.153722
2022-03-02    0.165544
2022-03-03    0.185017
2022-03-04    0.147672
2022-03-07    0.139172
2022-03-08    0.149522
2022-03-09    0.147417
2022-03-10    0.167033
2022-03-11    0.151850
2022-03-14    0.164850
2022-03-15    0.139950
2022-03-16    0.162033
2022-03-17    0.173739
2022-03-18    0.168578
2022-03-21    0.167278
2022-03-22    0.165106
2022-03-23    0.161211
2022-03-24    0.163133
2022-03-25    0.155261
2022-03-28    0.159511
2022-03-29    0.156211
2022-03-30    0.168900
2022-03-31    0.153672
2022-04-01    0.168411
2022-04-04    0.150511
2022-04-05    0.152678
2022-0

#####3 months
***

In [ ]:
t_3m=pred(q1_1,134)
t_3m=pd.DataFrame.from_dict(t_3m)
t_3m.set_index('date')
RPS_3m= RPS_data(t_3m,rd)
RPS_3m= create_RPS(t_3m,RPS_3m)
RPS_3m
print(RPS_3m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-03-23    5
Name: UNH, dtype: int64 mikos 60
5 defaultdict(<class 'int'>, {3: 17, 2: 11, 1: 7, 4: 14, 5: 11})
imera : 2022-03-25
arxi insample Date
2021-12-29    3
Name: UNH, dtype: int64 kai telos insample Date
2022-03-23    5
2022-03-24    1
Name: UNH, dtype: int64 mikos 60
1 defaultdict(<class 'int'>, {3: 16, 2: 11, 1: 8, 4: 14, 5: 11})
imera : 2022-03-28
arxi insample Date
2021-12-30    2
Name: UNH, dtype: int64 kai telos insample Date
2022-03-24    1
2022-03-25    2
Name: UNH, dtype: int64 mikos 60
2 defaultdict(<class 'int'>, {2: 12, 3: 15, 1: 8, 4: 14, 5: 11})
imera : 2022-03-29
arxi insample Date
2021-12-31    3
Name: UNH, dtype: int64 kai telos insample Date
2022-03-25    2
2022-03-28    1
Name: UNH, dtype: int64 mikos 60
1 defaultdict(<class 'int'>, {3: 15, 1: 9, 4: 14, 2: 11, 5: 11})
imera : 2022-03-30
arxi insample Date
2022-01-03    1
Name: UNH, dtype: int64 kai telos insample Date
2022-03-28    1
2022-03-29    5
N

In [ ]:
RPS_3m.mean(axis=1)

date
2022-02-03    0.170193
2022-02-04    0.170096
2022-02-07    0.153123
2022-02-08    0.156570
2022-02-09    0.156696
2022-02-10    0.167694
2022-02-11    0.176331
2022-02-14    0.160711
2022-02-15    0.172254
2022-02-16    0.151185
2022-02-17    0.168212
2022-02-18    0.150528
2022-02-22    0.161405
2022-02-23    0.151398
2022-02-24    0.178909
2022-02-25    0.175756
2022-02-28    0.143780
2022-03-01    0.151005
2022-03-02    0.161958
2022-03-03    0.176415
2022-03-04    0.142689
2022-03-07    0.138336
2022-03-08    0.147973
2022-03-09    0.146617
2022-03-10    0.164864
2022-03-11    0.154141
2022-03-14    0.165128
2022-03-15    0.140696
2022-03-16    0.157526
2022-03-17    0.176644
2022-03-18    0.159983
2022-03-21    0.157193
2022-03-22    0.159146
2022-03-23    0.171909
2022-03-24    0.151074
2022-03-25    0.154514
2022-03-28    0.161662
2022-03-29    0.151837
2022-03-30    0.169244
2022-03-31    0.148136
2022-04-01    0.164109
2022-04-04    0.144467
2022-04-05    0.149477
2022-0

#####6 months
***

In [ ]:
t_6m=pred(q1_1,74)
t_6m=pd.DataFrame.from_dict(t_6m)
t_6m.set_index('date')
RPS_6m= RPS_data(t_6m,rd)
RPS_6m= create_RPS(t_6m,RPS_6m)
RPS_6m
print(RPS_6m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
arxi insample Date
2021-08-19    1
Name: URI, dtype: int64 kai telos insample Date
2022-02-07    5
2022-02-08    5
Name: URI, dtype: int64 mikos 120
--------------------------------------------------------------- False
5 defaultdict(<class 'int'>, {1: 36, 5: 30, 3: 19, 2: 18, 4: 17})
imera : 2022-02-10
arxi insample Date
2021-08-20    5
Name: URI, dtype: int64 kai telos insample Date
2022-02-08    5
2022-02-09    1
Name: URI, dtype: int64 mikos 120
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {5: 30, 3: 19, 2: 18, 1: 36, 4: 17})
imera : 2022-02-11
arxi insample Date
2021-08-23    5
Name: URI, dtype: int64 kai telos insample Date
2022-02-09    1
2022-02-10    1
Name: URI, dtype: int64 mikos 120
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {5: 29, 3: 19, 2: 18, 1: 37, 4: 17})
imera : 2022-02-14
arxi insample Date
2021-08-24    

In [ ]:
RPS_6m.mean(axis=1)

date
2022-02-03    0.161681
2022-02-04    0.161276
2022-02-07    0.157554
2022-02-08    0.159973
2022-02-09    0.158315
2022-02-10    0.159683
2022-02-11    0.161341
2022-02-14    0.156356
2022-02-15    0.161906
2022-02-16    0.154933
2022-02-17    0.165060
2022-02-18    0.150874
2022-02-22    0.161047
2022-02-23    0.151541
2022-02-24    0.166544
2022-02-25    0.169040
2022-02-28    0.148089
2022-03-01    0.157662
2022-03-02    0.161981
2022-03-03    0.169568
2022-03-04    0.146770
2022-03-07    0.146151
2022-03-08    0.150108
2022-03-09    0.149437
2022-03-10    0.168048
2022-03-11    0.152545
2022-03-14    0.163682
2022-03-15    0.149206
2022-03-16    0.156452
2022-03-17    0.170108
2022-03-18    0.155886
2022-03-21    0.152917
2022-03-22    0.160975
2022-03-23    0.163369
2022-03-24    0.151014
2022-03-25    0.155044
2022-03-28    0.160693
2022-03-29    0.160007
2022-03-30    0.167005
2022-03-31    0.153109
2022-04-01    0.163518
2022-04-04    0.148928
2022-04-05    0.149662
2022-0

#####All the samples
***

In [ ]:
t_all=pred2(q1_1)
t_all=pd.DataFrame.from_dict(t_all)
t_all.set_index('date')
RPS_all= RPS_data(t_all,rd)
RPS_all= create_RPS(t_all,RPS_all)
RPS_all
print(RPS_all.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
[datetime.date(2022, 2, 4), datetime.date(2022, 2, 7), datetime.date(2022, 2, 8), datetime.date(2022, 2, 9), datetime.date(2022, 2, 10), datetime.date(2022, 2, 11), datetime.date(2022, 2, 14), datetime.date(2022, 2, 15), datetime.date(2022, 2, 16), datetime.date(2022, 2, 17), datetime.date(2022, 2, 18), datetime.date(2022, 2, 22), datetime.date(2022, 2, 23), datetime.date(2022, 2, 24), datetime.date(2022, 2, 25), datetime.date(2022, 2, 28), datetime.date(2022, 3, 1), datetime.date(2022, 3, 2), datetime.date(2022, 3, 3), datetime.date(2022, 3, 4), datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18), datetime.date(2022, 3, 21), datetime.date(2022, 3, 22), datetime.date(2022, 3, 23), datetime.date(2022, 3, 24), dat

In [ ]:
RPS_all.mean(axis=1)

date
2022-02-04    0.159867
2022-02-07    0.158183
2022-02-08    0.158603
2022-02-09    0.158076
2022-02-10    0.158031
2022-02-11    0.159047
2022-02-14    0.157344
2022-02-15    0.157709
2022-02-16    0.156331
2022-02-17    0.159451
2022-02-18    0.155524
2022-02-22    0.161172
2022-02-23    0.155126
2022-02-24    0.161102
2022-02-25    0.161154
2022-02-28    0.154010
2022-03-01    0.160643
2022-03-02    0.162510
2022-03-03    0.162483
2022-03-04    0.153272
2022-03-07    0.153962
2022-03-08    0.154907
2022-03-09    0.154513
2022-03-10    0.165011
2022-03-11    0.155866
2022-03-14    0.161608
2022-03-15    0.155153
2022-03-16    0.154164
2022-03-17    0.162133
2022-03-18    0.158526
2022-03-21    0.158356
2022-03-22    0.162535
2022-03-23    0.157768
2022-03-24    0.157266
2022-03-25    0.156560
2022-03-28    0.157580
2022-03-29    0.162165
2022-03-30    0.161373
2022-03-31    0.154901
2022-04-01    0.160513
2022-04-04    0.154931
2022-04-05    0.154414
2022-04-06    0.158925
2022-0